In [ ]:
import numpy as np
import pandas as pd
from sklearn.model_selection import train_test_split

from numpy import mean
from numpy import std

from matplotlib import pyplot
from sklearn.metrics import accuracy_score,confusion_matrix,classification_report
from sklearn.preprocessing import QuantileTransformer
from sklearn.pipeline import Pipeline

from scipy.stats import mode

In [ ]:
!nvidia-smi  

Sun Apr 24 15:09:55 2022       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 460.32.03    Driver Version: 460.32.03    CUDA Version: 11.2     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|                               |                      |               MIG M. |
|===============================+======================+======================|
|   0  Tesla V100-SXM2...  Off  | 00000000:00:04.0 Off |                    0 |
| N/A   33C    P0    24W / 300W |      0MiB / 16160MiB |      0%      Default |
|                               |                      |                  N/A |
+-------------------------------+----------------------+----------------------+
                                                                               
+-------

In [ ]:
from pydrive.auth import GoogleAuth
from pydrive.drive import GoogleDrive
from google.colab import auth
from oauth2client.client import GoogleCredentials

In [ ]:
auth.authenticate_user()
gauth = GoogleAuth()
gauth.credentials = GoogleCredentials.get_application_default()
drive = GoogleDrive(gauth)

In [ ]:
#npz files can only be loaded using /gdrive path
from google.colab import drive
drive.mount('/content/gdrive')
#%cd /gdrive

Mounted at /content/gdrive


In [ ]:
!pip install mne

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 7.5 MB 1.3 MB/s 


In [ ]:
#import pyeeg
from tensorflow import keras 

In [ ]:
%matplotlib inline

import glob
import math
import ntpath
import random, os, sys
import numpy as np
import pandas as pd
import tensorflow as tf
import matplotlib.pyplot as plt
import seaborn as sns
#import edfreader
#import models
import mne
#import pyeeg
import warnings
warnings.filterwarnings('ignore')

from matplotlib.backends.backend_pdf import PdfPages
from mne.datasets.sleep_physionet._utils import _fetch_one, _data_path, AGE_SLEEP_RECORDS, _check_subjects
from datetime import datetime
from mne import Epochs, pick_types, find_events
from mne.io import concatenate_raws, read_raw_edf
from mne.time_frequency import psd_welch
from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import classification_report

from tqdm.notebook import tqdm
from sklearn.model_selection import train_test_split
from tensorflow import keras

from tensorflow.keras.utils import to_categorical

from tensorflow.keras.callbacks import ModelCheckpoint, ReduceLROnPlateau, CSVLogger
import imblearn
from imblearn.over_sampling import SMOTE
from sklearn.svm import SVC
import joblib

from sklearn.metrics import make_scorer, f1_score, accuracy_score, classification_report, log_loss
from sklearn.metrics import roc_auc_score, confusion_matrix, roc_auc_score, roc_curve

from sklearn.tree import DecisionTreeClassifier
from sklearn.neighbors import KNeighborsClassifier
from sklearn.ensemble import RandomForestClassifier, AdaBoostClassifier, GradientBoostingClassifier
from sklearn.naive_bayes import GaussianNB
from sklearn.discriminant_analysis import LinearDiscriminantAnalysis
from sklearn.discriminant_analysis import QuadraticDiscriminantAnalysis
#from xgboost import XGBClassifier
#import xgboost

In [ ]:
VBS = True  # constant boolean to enable/disbale verbose
EPOCH_SEC_SIZE = 30  # Epoch duration selection
seed = 42  # seed value for the random seeds
batch_size = 64
number_of_files = 100 #100 npz files, 50 subjects, each suject has 2 nights, so 2 files per subject (50*2)=100

# values to label the stages
UNKNOWN = -1
W = 0
N1 = 1
N2 = 2
N3 = 3
REM = 4

# making string dictionary for the label values
label_dict = {
    "UNKNOWN"  : UNKNOWN,
    "W"        : W,
    "N1"       : N1,
    "N2"       : N2,
    "N3"       : N3,
    "REM"      : REM
}

# converting from label values to strings 
class_dict = {
    -1: "UNKNOWN",
    0 : "W",
    1 : "N1",
    2 : "N2",
    3 : "N3",
    4 : "REM"
}

# annotation dictionary to convert from string to label values
annot2label = {
    "Sleep stage ?": -1,
    "Movement time": -1,
    "Sleep stage W": 0,
    "Sleep stage 1": 1,
    "Sleep stage 2": 2,
    "Sleep stage 3": 3,
    "Sleep stage 4": 3,
    "Sleep stage R": 4
}
#project_path = os.path.abspath(os.getcwd())  # finding the current project path in windows

In [ ]:
from tensorflow.keras import optimizers, losses, activations, models
from tensorflow.keras.models import Model, load_model
from tensorflow.keras.layers import GlobalMaxPool1D, GlobalAveragePooling1D, concatenate, SpatialDropout1D, TimeDistributed, Bidirectional, LSTM
from tensorflow.keras.layers import Input, Conv1D, Dense, Dropout, MaxPool1D, Activation
from tensorflow.keras.layers import Reshape, LSTM, TimeDistributed, Bidirectional, BatchNormalization, Flatten, RepeatVector
from tensorflow.keras.optimizers import Adam
#from keras_contrib.layers import CRF

from scipy.signal import butter, lfilter


In [ ]:
Fs = 100
from keras.utils import np_utils

In [ ]:
subject_482_df=pd.read_csv('/content/gdrive/My Drive/physionet/ensemble/50_subs/subject_482_dataset.csv',header=None)

In [ ]:
x_sub_set=subject_482_df.drop([3000],axis=1)

In [ ]:
x_sub_set

In [ ]:
y_sub_dt=subject_482_df[3000]

In [ ]:
y_sub_dt

In [ ]:
x_train_sub,x_test_sub,y_train_sub,y_test_sub=train_test_split(x_sub_set,y_sub_dt,test_size=0.2,random_state=100)

In [ ]:
pip install git+https://www.github.com/keras-team/keras-contrib.git

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
  Cloning https://www.github.com/keras-team/keras-contrib.git to /tmp/pip-req-build-gbbpaq1l
  Running command git clone -q https://www.github.com/keras-team/keras-contrib.git /tmp/pip-req-build-gbbpaq1l
  Created wheel for keras-contrib: filename=keras_contrib-2.0.8-py3-none-any.whl size=101077 sha256=8f6c1a8ff2d32bdc5bc4d9adcf2662a01d0d3d4b73fe38cb9f4d8626d91614b3
  Stored in directory: /tmp/pip-ephem-wheel-cache-op74gahg/wheels/bb/1f/f2/b57495012683b6b20bbae94a3915ec79753111452d79886abc
Successfully built keras-contrib


In [ ]:
from keras import optimizers, losses, activations, models
from keras.layers import Dense, Input, Dropout, Convolution1D, MaxPool1D, GlobalMaxPool1D, GlobalAveragePooling1D, concatenate, SpatialDropout1D, TimeDistributed, Bidirectional, LSTM
from keras_contrib.layers import CRF

WINDOW_SIZE = 100

optimizer = Adam(lr=1e-4)

from scipy.stats import mode

In [ ]:
nclass = 5

#n_classes=5
def model_b(n_classes=5, use_sub_layer=False, use_rnn=True, verbose=False):
    inputLayer = Input(shape=(3000, 1), name='inLayer')
    convFine = Conv1D(filters=64, kernel_size=int(Fs/2), strides=int(Fs/16), padding='same', activation='relu', name='fConv1')(inputLayer)
    convFine = MaxPool1D(pool_size=8, strides=8, name='fMaxP1')(convFine)
    convFine = Dropout(rate=0.5, name='fDrop1')(convFine)
    convFine = Conv1D(filters=128, kernel_size=8, padding='same', activation='relu', name='fConv2')(convFine)
    convFine = Conv1D(filters=128, kernel_size=8, padding='same', activation='relu', name='fConv3')(convFine)
    convFine = Conv1D(filters=128, kernel_size=8, padding='same', activation='relu', name='fConv4')(convFine)
    convFine = MaxPool1D(pool_size=4, strides=4, name='fMaxP2')(convFine)
    fineShape = convFine.get_shape()
    convFine = Flatten(name='fFlat1')(convFine)
    
    # network to learn coarse features
    convCoarse = Conv1D(filters=32, kernel_size=Fs*4, strides=int(Fs/2), padding='same', activation='relu', name='cConv1')(inputLayer)
    convCoarse = MaxPool1D(pool_size=4, strides=4, name='cMaxP1')(convCoarse)
    convCoarse = Dropout(rate=0.5, name='cDrop1')(convCoarse)
    convCoarse = Conv1D(filters=128, kernel_size=6, padding='same', activation='relu', name='cConv2')(convCoarse)
    convCoarse = Conv1D(filters=128, kernel_size=6, padding='same', activation='relu', name='cConv3')(convCoarse)
    convCoarse = Conv1D(filters=128, kernel_size=6, padding='same', activation='relu', name='cConv4')(convCoarse)
    convCoarse = MaxPool1D(pool_size=2, strides=2, name='cMaxP2')(convCoarse)
    coarseShape = convCoarse.get_shape()
    convCoarse = Flatten(name='cFlat1')(convCoarse)
    
    # concatenate coarse and fine cnns
    mergeLayer = concatenate([convFine, convCoarse], name='merge_1')
    outLayer = Dropout(rate=0.5, name='mDrop1')(mergeLayer)
    
    outLayer = Reshape((1, outLayer.get_shape()[1]), name='reshape1')(outLayer)
    outLayer = LSTM(64, return_sequences=True)(outLayer)
    outLayer = LSTM(64, return_sequences=False)(outLayer)

    # Classify
    outLayer = Dense(n_classes, activation='softmax', name='outLayer')(outLayer)
    model = Model(inputLayer, outLayer)
    optimizer = Adam(lr=1e-4)
    model.compile(optimizer=optimizer, loss='categorical_crossentropy', metrics=['acc'])
    #model.compile(optimizer=optimizer, loss='categorical_crossentropy', metrics=['accuracy'])
    if verbose:
        model.summary()
    return model

In [ ]:
loaded_model_shuf1=model_b(verbose=VBS)
loaded_model_shuf2=model_b(verbose=VBS)
loaded_model_shuf3=model_b(verbose=VBS)

Model: "model"
__________________________________________________________________________________________________
 Layer (type)                   Output Shape         Param #     Connected to                     
 inLayer (InputLayer)           [(None, 3000, 1)]    0           []                               
                                                                                                  
 fConv1 (Conv1D)                (None, 500, 64)      3264        ['inLayer[0][0]']                
                                                                                                  
 cConv1 (Conv1D)                (None, 60, 32)       12832       ['inLayer[0][0]']                
                                                                                                  
 fMaxP1 (MaxPooling1D)          (None, 62, 64)       0           ['fConv1[0][0]']                 
                                                                                              

In [ ]:
#dt_shuf1
checkpoint_path_load_model_30_epochs_shuf1 = "/content/gdrive/My Drive/physionet/dt_shuf1_phy/sub_482_75th_sub_with_50_sub_tr_dt/weights-phy_shuf1_30_epochs.ckpt"
checkpoint_load_model_30_epochs_shuf1_dir = os.path.dirname(checkpoint_path_load_model_30_epochs_shuf1)
#latest_30_epochs_shuf1_s828=tensorflow.train.latest_checkpoint(checkpoint_load_model_300_epochs_shuf1_s828_dir)
print(checkpoint_path_load_model_30_epochs_shuf1)

/content/gdrive/My Drive/physionet/dt_shuf1_phy/sub_482_75th_sub_with_50_sub_tr_dt/weights-phy_shuf1_30_epochs.ckpt


In [ ]:
#dt_shuf2
checkpoint_path_load_model_30_epochs_shuf2 = "/content/gdrive/My Drive/physionet/dt_shuf2_phy/sub_482_75th_sub_with_50_sub_tr_dt/weights-phy_shuf2_30_epochs.ckpt"
checkpoint_load_model_30_epochs_shuf2_dir = os.path.dirname(checkpoint_path_load_model_30_epochs_shuf2)
#latest_300_epochs_shuf2_s828=tensorflow.train.latest_checkpoint(checkpoint_load_model_300_epochs_shuf2_s828_dir)
print(checkpoint_path_load_model_30_epochs_shuf2)

/content/gdrive/My Drive/physionet/dt_shuf2_phy/sub_482_75th_sub_with_50_sub_tr_dt/weights-phy_shuf2_30_epochs.ckpt


In [ ]:
#dt_shuf3
checkpoint_path_load_model_30_epochs_shuf3 = "/content/gdrive/My Drive/physionet/dt_shuf3_phy/sub_482_75th_sub_with_50_sub_tr_dt/weights-phy_shuf3_30_epochs.ckpt"
checkpoint_load_model_30_epochs_shuf3_dir = os.path.dirname(checkpoint_path_load_model_30_epochs_shuf3)
#latest_300_epochs_shuf3_s828=tensorflow.train.latest_checkpoint(checkpoint_load_model_300_epochs_shuf3_s828_dir)
print(checkpoint_path_load_model_30_epochs_shuf3)

/content/gdrive/My Drive/physionet/dt_shuf3_phy/sub_482_75th_sub_with_50_sub_tr_dt/weights-phy_shuf3_30_epochs.ckpt


In [ ]:
loaded_model_shuf1.load_weights(checkpoint_path_load_model_30_epochs_shuf1)
loaded_model_shuf2.load_weights(checkpoint_path_load_model_30_epochs_shuf2)
loaded_model_shuf3.load_weights(checkpoint_path_load_model_30_epochs_shuf3)

In [ ]:
for i,layer in enumerate(loaded_model_shuf1.layers):
  print(i,layer.name)

0 inLayer
1 fConv1
2 cConv1
3 fMaxP1
4 cMaxP1
5 fDrop1
6 cDrop1
7 fConv2
8 cConv2
9 fConv3
10 cConv3
11 fConv4
12 cConv4
13 fMaxP2
14 cMaxP2
15 fFlat1
16 cFlat1
17 merge_1
18 mDrop1
19 reshape1
20 lstm
21 lstm_1
22 outLayer


In [ ]:
for i,layer in enumerate(loaded_model_shuf1.layers):
  print(i,layer.name,layer.trainable)

0 inLayer True
1 fConv1 True
2 cConv1 True
3 fMaxP1 True
4 cMaxP1 True
5 fDrop1 True
6 cDrop1 True
7 fConv2 True
8 cConv2 True
9 fConv3 True
10 cConv3 True
11 fConv4 True
12 cConv4 True
13 fMaxP2 True
14 cMaxP2 True
15 fFlat1 True
16 cFlat1 True
17 merge_1 True
18 mDrop1 True
19 reshape1 True
20 lstm True
21 lstm_1 True
22 outLayer True


In [ ]:
for layer in loaded_model_shuf1.layers[:23]:
  layer.trainable=False
#for layer in loaded_model_shuf1.layers[20:]:
 # layer.trainable=False

In [ ]:
for i,layer in enumerate(loaded_model_shuf1.layers):
  print(i,layer.name,layer.trainable)

0 inLayer False
1 fConv1 False
2 cConv1 False
3 fMaxP1 False
4 cMaxP1 False
5 fDrop1 False
6 cDrop1 False
7 fConv2 False
8 cConv2 False
9 fConv3 False
10 cConv3 False
11 fConv4 False
12 cConv4 False
13 fMaxP2 False
14 cMaxP2 False
15 fFlat1 False
16 cFlat1 False
17 merge_1 False
18 mDrop1 False
19 reshape1 False
20 lstm False
21 lstm_1 False
22 outLayer False


In [ ]:
for layer in loaded_model_shuf2.layers[:23]:
  layer.trainable=False
#for layer in loaded_model_shuf2.layers[20:]:
 # layer.trainable=False

In [ ]:
for layer in loaded_model_shuf3.layers[:23]:
  layer.trainable=False
#for layer in loaded_model_shuf3.layers[20:]:
#  layer.trainable=False

In [ ]:
for i,layer in enumerate(loaded_model_shuf2.layers):
  print(i,layer.name,layer.trainable)

0 inLayer False
1 fConv1 False
2 cConv1 False
3 fMaxP1 False
4 cMaxP1 False
5 fDrop1 False
6 cDrop1 False
7 fConv2 False
8 cConv2 False
9 fConv3 False
10 cConv3 False
11 fConv4 False
12 cConv4 False
13 fMaxP2 False
14 cMaxP2 False
15 fFlat1 False
16 cFlat1 False
17 merge_1 False
18 mDrop1 False
19 reshape1 False
20 lstm_2 False
21 lstm_3 False
22 outLayer False


In [ ]:
for i,layer in enumerate(loaded_model_shuf3.layers):
  print(i,layer.name,layer.trainable)

0 inLayer False
1 fConv1 False
2 cConv1 False
3 fMaxP1 False
4 cMaxP1 False
5 fDrop1 False
6 cDrop1 False
7 fConv2 False
8 cConv2 False
9 fConv3 False
10 cConv3 False
11 fConv4 False
12 cConv4 False
13 fMaxP2 False
14 cMaxP2 False
15 fFlat1 False
16 cFlat1 False
17 merge_1 False
18 mDrop1 False
19 reshape1 False
20 lstm_4 False
21 lstm_5 False
22 outLayer False


In [ ]:
loaded_model_shuf1.compile(optimizer=optimizer, loss='categorical_crossentropy', metrics=['accuracy'])
loaded_model_shuf2.compile(optimizer=optimizer, loss='categorical_crossentropy', metrics=['accuracy'])
loaded_model_shuf3.compile(optimizer=optimizer, loss='categorical_crossentropy', metrics=['accuracy'])

In [ ]:
print(loaded_model_shuf1.summary())
print(loaded_model_shuf2.summary())
print(loaded_model_shuf3.summary())

Model: "model"
__________________________________________________________________________________________________
 Layer (type)                   Output Shape         Param #     Connected to                     
 inLayer (InputLayer)           [(None, 3000, 1)]    0           []                               
                                                                                                  
 fConv1 (Conv1D)                (None, 500, 64)      3264        ['inLayer[0][0]']                
                                                                                                  
 cConv1 (Conv1D)                (None, 60, 32)       12832       ['inLayer[0][0]']                
                                                                                                  
 fMaxP1 (MaxPooling1D)          (None, 62, 64)       0           ['fConv1[0][0]']                 
                                                                                              

In [ ]:
x_train_sub.shape

In [ ]:
x_train_sub

0         1         2     ...      2997      2998      2999
774  -0.037317 -0.035184 -0.053523  ... -0.056081 -0.107685 -0.138817
2812  0.022085 -0.017796 -0.064110  ... -0.084265 -0.057249 -0.053389
2615 -0.127577 -0.109566 -0.066254  ...  0.021656  0.037094  0.021656
2706 -0.147303 -0.149447 -0.105278  ...  0.111710  0.105278  0.122860
1479 -0.071861 -0.088920 -0.128156  ... -0.012581 -0.015140  0.001919
...        ...       ...       ...  ...       ...       ...       ...
1930 -0.002359  0.139156 -0.008791  ... -0.048672 -0.414036 -0.345852
79   -0.136259 -0.109391 -0.123891  ... -0.052243 -0.233495 -0.170376
1859  0.016081  0.049101 -0.076117  ... -0.027231  0.014366 -0.018225
2840 -0.009220 -0.006647 -0.006218  ...  0.073544  0.057678  0.033663
1544  0.007890 -0.079964 -0.121332  ...  0.136685  0.148626  0.104273

[2456 rows x 3000 columns]

In [ ]:
tf.config.run_functions_eagerly(True)

In [ ]:
x_train_sub[0:500]

In [ ]:
x_test_sub.shape

In [ ]:
train_dt=x_train_sub
train_dt['sleep_stage']=y_train_sub

In [ ]:
test_dt=x_test_sub
test_dt['sleep_stage']=y_test_sub

In [ ]:
train_dt.shape

In [ ]:
test_dt.shape

In [ ]:
test_dt.to_csv(r'/content/gdrive/My Drive/physionet/ensemble/50_subs/x_test_sub.csv', header=False, index=False)

In [ ]:
train_dt.to_csv(r'/content/gdrive/My Drive/physionet/ensemble/50_subs/x_train_sub.csv', header=False, index=False)

In [ ]:
tr_dt=pd.read_csv('/content/gdrive/My Drive/physionet/ensemble/50_subs/x_train_sub.csv', header=None)

In [ ]:
tr_dt

0         1         2         3         4         5         6     \
0    -0.037317 -0.035184 -0.053523 -0.013007  0.056081  0.106405  0.121332   
1     0.022085 -0.017796 -0.064110 -0.042669 -0.010506  0.002359 -0.012222   
2    -0.127577 -0.109566 -0.066254 -0.008791 -0.037952 -0.106564 -0.128006   
3    -0.147303 -0.149447 -0.105278 -0.070971 -0.057678 -0.042240 -0.037523   
4    -0.071861 -0.088920 -0.128156 -0.128156 -0.117920 -0.088067 -0.066743   
...        ...       ...       ...       ...       ...       ...       ...   
2451 -0.002359  0.139156 -0.008791  0.067970  0.106136  0.143015  0.113426   
2452 -0.136259 -0.109391 -0.123891 -0.130714 -0.159288 -0.149053 -0.161847   
2453  0.016081  0.049101 -0.076117 -0.019083 -0.055534 -0.042669 -0.136583   
2454 -0.009220 -0.006647 -0.006218 -0.010506  0.011364 -0.017368 -0.025515   
2455  0.007890 -0.079964 -0.121332 -0.080390 -0.072714 -0.021963  0.009596   

          7         8         9     ...      2991      2992      2993  \
0     0.129435  0.153744  0.198097  ... -0.088920 -0.118773 -0.130714   
1    -0.040524 -0.072258 -0.054247  ...  0.119858  0.074831 -0.004503   
2    -0.106993 -0.100132 -0.077833  ... -0.001501  0.037952  0.036665   
3    -0.040953 -0.046957 -0.017796  ...  0.239931  0.229639  0.205624   
4    -0.033478 -0.030919 -0.008743  ...  0.031772 -0.009596 -0.039875   
...        ...       ...       ...  ...       ...       ...       ...   
2451  0.005789  0.059822  0.031948  ... -0.274666 -0.113855 -0.155022   
2452 -0.102141 -0.091905 -0.026228  ... -0.175068 -0.268039 -0.137538   
2453 -0.041811 -0.082550 -0.010078  ... -0.121573 -0.110424 -0.085123   
2454 -0.032377 -0.011793  0.010935  ... -0.045242 -0.006218  0.029804   
2455  0.013434  0.027081 -0.027934  ...  0.027508  0.044567  0.044993   

          2994      2995      2996      2997      2998      2999  3000  
0    -0.128156 -0.092332 -0.072287 -0.056081 -0.107685 -0.138817     2  
1    -0.031090 -0.081263 -0.052103 -0.084265 -0.057249 -0.053389     4  
2     0.046528  0.048243  0.011364  0.021656  0.037094  0.021656     4  
3     0.192759  0.182039  0.137869  0.111710  0.105278  0.122860     2  
4    -0.053523 -0.083802 -0.053096 -0.012581 -0.015140  0.001919     2  
...        ...       ...       ...       ...       ...       ...   ...  
2451  0.121145 -0.032377  0.225350 -0.048672 -0.414036 -0.345852     0  
2452 -0.193406 -0.041581 -0.178906 -0.052243 -0.233495 -0.170376     0  
2453 -0.070114 -0.073544 -0.042240 -0.027231  0.014366 -0.018225     0  
2454  0.075260  0.103991  0.104420  0.073544  0.057678  0.033663     2  
2455  0.051817  0.078685  0.100435  0.136685  0.148626  0.104273     2  

[2456 rows x 3001 columns]

In [ ]:
x_sub_set=tr_dt.drop([3000],axis=1)
y_sub_dt=tr_dt[3000]

In [ ]:
loaded_model_shuf1_new=model_b(verbose=VBS)
loaded_model_shuf2_new=model_b(verbose=VBS)
loaded_model_shuf3_new=model_b(verbose=VBS)

Model: "model_3"
__________________________________________________________________________________________________
 Layer (type)                   Output Shape         Param #     Connected to                     
 inLayer (InputLayer)           [(None, 3000, 1)]    0           []                               
                                                                                                  
 fConv1 (Conv1D)                (None, 500, 64)      3264        ['inLayer[0][0]']                
                                                                                                  
 cConv1 (Conv1D)                (None, 60, 32)       12832       ['inLayer[0][0]']                
                                                                                                  
 fMaxP1 (MaxPooling1D)          (None, 62, 64)       0           ['fConv1[0][0]']                 
                                                                                            

In [ ]:
loaded_model_shuf1_new.load_weights(checkpoint_path_load_model_30_epochs_shuf1)
loaded_model_shuf2_new.load_weights(checkpoint_path_load_model_30_epochs_shuf2)
loaded_model_shuf3_new.load_weights(checkpoint_path_load_model_30_epochs_shuf3)

In [ ]:
for layer in loaded_model_shuf1_new.layers[:20]:
  layer.trainable=False
for layer in loaded_model_shuf1_new.layers[20:]:
  layer.trainable=True

In [ ]:
for layer in loaded_model_shuf2_new.layers[:20]:
  layer.trainable=False
for layer in loaded_model_shuf2_new.layers[20:]:
  layer.trainable=True

In [ ]:
for layer in loaded_model_shuf3_new.layers[:20]:
  layer.trainable=False
for layer in loaded_model_shuf3_new.layers[20:]:
  layer.trainable=True

In [ ]:
loaded_model_shuf1_new.compile(optimizer=optimizer, loss='categorical_crossentropy', metrics=['accuracy'])
loaded_model_shuf2_new.compile(optimizer=optimizer, loss='categorical_crossentropy', metrics=['accuracy'])
loaded_model_shuf3_new.compile(optimizer=optimizer, loss='categorical_crossentropy', metrics=['accuracy'])

In [ ]:
loaded_model_shuf1_new.summary()

Model: "model_3"
__________________________________________________________________________________________________
 Layer (type)                   Output Shape         Param #     Connected to                     
 inLayer (InputLayer)           [(None, 3000, 1)]    0           []                               
                                                                                                  
 fConv1 (Conv1D)                (None, 500, 64)      3264        ['inLayer[0][0]']                
                                                                                                  
 cConv1 (Conv1D)                (None, 60, 32)       12832       ['inLayer[0][0]']                
                                                                                                  
 fMaxP1 (MaxPooling1D)          (None, 62, 64)       0           ['fConv1[0][0]']                 
                                                                                            

In [ ]:
loaded_model_shuf2_new.summary()

Model: "model_4"
__________________________________________________________________________________________________
 Layer (type)                   Output Shape         Param #     Connected to                     
 inLayer (InputLayer)           [(None, 3000, 1)]    0           []                               
                                                                                                  
 fConv1 (Conv1D)                (None, 500, 64)      3264        ['inLayer[0][0]']                
                                                                                                  
 cConv1 (Conv1D)                (None, 60, 32)       12832       ['inLayer[0][0]']                
                                                                                                  
 fMaxP1 (MaxPooling1D)          (None, 62, 64)       0           ['fConv1[0][0]']                 
                                                                                            

In [ ]:
loaded_model_shuf3_new.summary()

Model: "model_5"
__________________________________________________________________________________________________
 Layer (type)                   Output Shape         Param #     Connected to                     
 inLayer (InputLayer)           [(None, 3000, 1)]    0           []                               
                                                                                                  
 fConv1 (Conv1D)                (None, 500, 64)      3264        ['inLayer[0][0]']                
                                                                                                  
 cConv1 (Conv1D)                (None, 60, 32)       12832       ['inLayer[0][0]']                
                                                                                                  
 fMaxP1 (MaxPooling1D)          (None, 62, 64)       0           ['fConv1[0][0]']                 
                                                                                            

##Incremental semi-supervised learning

In [ ]:
checkpoint_path_model_inc_shuf1 = "/content/gdrive/My Drive/physionet/ensemble_inc_semi_sup_learning/model_shuf1/weights-{epoch:02d}-{accuracy:.3f}.ckpt"
checkpoint_dir_model_inc_shuf1 = os.path.dirname(checkpoint_path_model_inc_shuf1)
cp_callback_model_new_shuf1 = tf.keras.callbacks.ModelCheckpoint(
    filepath=checkpoint_path_model_inc_shuf1,
    monitor='accuracy', 
    verbose=1, 
    save_weights_only=True,
    mode = 'max',
    period=1)

In [ ]:
checkpoint_path_model_inc_shuf2 = "/content/gdrive/My Drive/physionet/ensemble_inc_semi_sup_learning/model_shuf2/weights-{epoch:02d}-{accuracy:.3f}.ckpt"
checkpoint_dir_model_inc_shuf2 = os.path.dirname(checkpoint_path_model_inc_shuf2)
cp_callback_model_new_shuf2 = tf.keras.callbacks.ModelCheckpoint(
    filepath=checkpoint_path_model_inc_shuf2,
    monitor='accuracy', 
    verbose=1, 
    save_weights_only=True,
    mode = 'max',
    period=1)

In [ ]:
checkpoint_path_model_inc_shuf3 = "/content/gdrive/My Drive/physionet/ensemble_inc_semi_sup_learning/model_shuf3/weights-{epoch:02d}-{accuracy:.3f}.ckpt"
checkpoint_dir_model_inc_shuf3 = os.path.dirname(checkpoint_path_model_inc_shuf3)
cp_callback_model_new_shuf3 = tf.keras.callbacks.ModelCheckpoint(
    filepath=checkpoint_path_model_inc_shuf3,
    monitor='accuracy', 
    verbose=1, 
    save_weights_only=True,
    mode = 'max',
    period=1)

In [ ]:
preds_shuf1=[]
preds_inc_shuf1=[]
probabilities_shuf1=[]
probabilities_inc_shuf1=[]


count_shuf1=0

preds_shuf2=[]
preds_inc_shuf2=[]
probabilities_shuf2=[]
probabilities_inc_shuf2=[]

count_shuf2=0

preds_shuf3=[]
preds_inc_shuf3=[]
probabilities_shuf3=[]
probabilities_inc_shuf3=[]

count_shuf3=0

m_vote_inc=[]

m_vote=[]

count_status1=0
count_status2=0
count_status3=0

for sple in np.array(x_sub_set[0:2457]):

  sple_rshp=sple.reshape(1,3000,1)

  p1_i=loaded_model_shuf1.predict(sple_rshp)

  p1_i_fin=np.argmax(p1_i,axis=1)

  preds_shuf1.append(np.asscalar(p1_i_fin))

  probabilities_shuf1.append(p1_i) 

  
  
  p1_i_inc=loaded_model_shuf1_new.predict_on_batch(sple_rshp)

  p1_i_inc_fin=np.argmax(p1_i_inc,axis=1)

  
  #count_shuf1+=1

  p2_i=loaded_model_shuf2.predict(sple_rshp)

  p2_i_fin=np.argmax(p2_i,axis=1)

  preds_shuf2.append(np.asscalar(p2_i_fin))

  probabilities_shuf2.append(p2_i)

  
    
  p2_i_inc=loaded_model_shuf2_new.predict_on_batch(sple_rshp)

  p2_i_inc_fin=np.argmax(p2_i_inc,axis=1)

  
  #count_shuf2+=1

  p3_i=loaded_model_shuf3.predict(sple_rshp)

  p3_i_fin=np.argmax(p3_i,axis=1)

  preds_shuf3.append(np.asscalar(p3_i_fin))

  probabilities_shuf3.append(p3_i)

  count_status3+=1

  
  p3_i_inc=loaded_model_shuf3_new.predict_on_batch(sple_rshp)

  p3_i_inc_fin=np.argmax(p3_i_inc,axis=1)


  

  preds_inc_shuf1.append(np.asscalar(p1_i_inc_fin))

  probabilities_inc_shuf1.append(p1_i_inc)


  preds_inc_shuf2.append(np.asscalar(p2_i_inc_fin))

  probabilities_inc_shuf2.append(p2_i_inc)


  preds_inc_shuf3.append(np.asscalar(p3_i_inc_fin))

  probabilities_inc_shuf3.append(p3_i_inc)


  mode_i_inc=mode([np.asscalar(p1_i_inc_fin),np.asscalar(p2_i_inc_fin),np.asscalar(p3_i_inc_fin)])
  m_vote_i_inc=mode_i_inc[0][0]
  m_vote_inc.append(m_vote_i_inc)

  mode_i=mode([np.asscalar(p1_i_fin),np.asscalar(p2_i_fin),np.asscalar(p3_i_fin)])
  m_vote_i=mode_i[0][0]
  m_vote.append(m_vote_i)



  p1_i_inc_fin_=np_utils.to_categorical(np.asscalar(p1_i_inc_fin), num_classes=5)
  p2_i_inc_fin_=np_utils.to_categorical(np.asscalar(p2_i_inc_fin), num_classes=5)
  p3_i_inc_fin_=np_utils.to_categorical(np.asscalar(p3_i_inc_fin), num_classes=5)

  p1_i_inc_fin_.shape=(1,5)
  p2_i_inc_fin_.shape=(1,5)
  p3_i_inc_fin_.shape=(1,5)


  p1_i_fin_=np_utils.to_categorical(np.asscalar(p1_i_fin), num_classes=5)
  p2_i_fin_=np_utils.to_categorical(np.asscalar(p2_i_fin), num_classes=5)
  p3_i_fin_=np_utils.to_categorical(np.asscalar(p3_i_fin), num_classes=5)

  p1_i_fin_.shape=(1,5)
  p2_i_fin_.shape=(1,5)
  p3_i_fin_.shape=(1,5)



  

  if p1_i_inc_fin == p1_i_fin:

   
    
        
    loaded_model_shuf1_new.train_on_batch(sple_rshp, p1_i_inc_fin_)

    

  if p1_i_inc_fin != p1_i_fin:

    p1_i_inc_fin=p1_i_fin

    p1_i_inc_fin_=np_utils.to_categorical(np.asscalar(p1_i_inc_fin), num_classes=5)

    p1_i_inc_fin_.shape=(1,5)

    
    loaded_model_shuf1_new.train_on_batch(sple_rshp, p1_i_inc_fin_)

   

  
  if p2_i_inc_fin == p2_i_fin:
   
      
    
    loaded_model_shuf2_new.train_on_batch(sple_rshp, p2_i_inc_fin_)

    

  if p2_i_inc_fin != p2_i_fin:

    p2_i_inc_fin=p2_i_fin

    p2_i_inc_fin_=np_utils.to_categorical(np.asscalar(p2_i_inc_fin), num_classes=5)

    p2_i_inc_fin_.shape=(1,5)


        
    loaded_model_shuf2_new.train_on_batch(sple_rshp, p2_i_inc_fin_)

    
  

  if p3_i_inc_fin == p3_i_fin:

    
        
    loaded_model_shuf3_new.train_on_batch(sple_rshp, p3_i_inc_fin_)

    

  if p3_i_inc_fin != p3_i_fin:

    p3_i_inc_fin=p3_i_fin

    p3_i_inc_fin_=np_utils.to_categorical(np.asscalar(p3_i_inc_fin), num_classes=5)

    p3_i_inc_fin_.shape=(1,5)


    
    loaded_model_shuf3_new.train_on_batch(sple_rshp, p3_i_inc_fin_)

     


  


In [ ]:
print(m_vote)
print(m_vote_inc)

[2, 2, 4, 2, 2, 0, 0, 2, 2, 2, 3, 3, 0, 4, 0, 3, 2, 0, 2, 0, 4, 0, 0, 4, 0, 0, 0, 2, 4, 2, 0, 2, 4, 2, 0, 0, 4, 2, 1, 2, 3, 0, 2, 2, 0, 3, 0, 0, 2, 2, 2, 4, 2, 2, 4, 0, 0, 0, 0, 0, 4, 3, 0, 0, 1, 0, 2, 2, 0, 0, 2, 0, 2, 2, 0, 0, 0, 2, 0, 0, 2, 1, 2, 2, 0, 0, 0, 0, 0, 2, 1, 2, 2, 3, 2, 0, 3, 0, 2, 4, 2, 0, 2, 2, 2, 2, 0, 0, 3, 0, 4, 2, 0, 0, 4, 0, 0, 2, 0, 0, 0, 0, 0, 0, 0, 0, 0, 2, 0, 0, 0, 0, 0, 4, 2, 2, 0, 0, 0, 0, 3, 0, 0, 0, 2, 0, 2, 0, 0, 2, 2, 4, 1, 2, 0, 2, 2, 0, 2, 0, 2, 0, 0, 3, 1, 2, 0, 4, 0, 2, 0, 0, 2, 3, 4, 2, 4, 2, 0, 2, 0, 0, 1, 0, 2, 2, 2, 0, 2, 4, 3, 0, 3, 2, 2, 2, 2, 3, 0, 2, 0, 3, 2, 4, 0, 3, 2, 2, 2, 4, 0, 2, 4, 0, 0, 0, 2, 0, 0, 4, 0, 0, 0, 2, 0, 4, 0, 4, 0, 2, 3, 3, 3, 2, 3, 2, 2, 1, 4, 2, 3, 4, 0, 0, 0, 0, 4, 0, 3, 0, 2, 3, 2, 4, 3, 2, 0, 0, 2, 2, 3, 0, 4, 2, 0, 0, 0, 2, 0, 0, 0, 3, 0, 2, 2, 0, 0, 2, 2, 0, 3, 2, 0, 0, 0, 2, 0, 0, 0, 2, 4, 0, 2, 0, 0, 0, 4, 0, 2, 4, 2, 0, 1, 0, 0, 2, 0, 2, 0, 4, 2, 4, 2, 0, 0, 2, 0, 0, 4, 0, 2, 4, 2, 0, 3, 0, 4, 0, 2, 2, 0, 0, 3, 

In [ ]:
print(probabilities_inc_shuf1)
print(probabilities_inc_shuf2)
print(probabilities_inc_shuf3)

Streaming output truncated to the last 5000 lines.
        2.7333064e-05]], dtype=float32), array([[9.9956530e-01, 2.9518630e-04, 6.2732142e-05, 4.5667864e-05,
        3.1153173e-05]], dtype=float32), array([[5.2849718e-05, 3.2016129e-04, 9.8325461e-01, 1.4599743e-02,
        1.7727062e-03]], dtype=float32), array([[9.9951780e-01, 3.6258108e-04, 6.0660419e-05, 3.4240566e-05,
        2.4763001e-05]], dtype=float32), array([[1.3466268e-05, 4.2360649e-04, 9.9856180e-01, 7.1219640e-04,
        2.8884699e-04]], dtype=float32), array([[7.5486038e-05, 1.9209173e-03, 1.2377579e-02, 3.3353343e-05,
        9.8559266e-01]], dtype=float32), array([[9.9967802e-01, 1.9092427e-04, 5.1379026e-05, 6.5489927e-05,
        1.4238746e-05]], dtype=float32), array([[9.9320579e-01, 5.7703159e-03, 8.3486288e-04, 3.9306498e-05,
        1.4974504e-04]], dtype=float32), array([[3.9972929e-05, 1.1846983e-03, 9.9697363e-01, 6.3892156e-05,
        1.7377465e-03]], dtype=float32), array([[9.9952638e-01, 3.6044591e-04

In [ ]:
print(probabilities_shuf1)
print(probabilities_shuf2)
print(probabilities_shuf3)

Streaming output truncated to the last 5000 lines.
        2.8658993e-04]], dtype=float32), array([[9.9893969e-01, 3.2339172e-04, 4.7321085e-04, 9.4169627e-05,
        1.6939642e-04]], dtype=float32), array([[1.6068602e-04, 9.9565065e-04, 8.5320187e-01, 1.4440058e-01,
        1.2412835e-03]], dtype=float32), array([[9.97947156e-01, 1.59555301e-03, 3.31521558e-04, 1.34054735e-05,
        1.12480004e-04]], dtype=float32), array([[2.9182529e-05, 2.3514153e-03, 9.9627328e-01, 5.0847570e-04,
        8.3760347e-04]], dtype=float32), array([[2.3999158e-03, 6.0397580e-02, 2.5356913e-01, 6.2655454e-05,
        6.8357074e-01]], dtype=float32), array([[9.9971205e-01, 1.7999674e-04, 6.9415240e-05, 2.7697135e-05,
        1.0903364e-05]], dtype=float32), array([[9.9420834e-01, 4.1619278e-03, 1.4337271e-03, 4.3201246e-05,
        1.5281695e-04]], dtype=float32), array([[1.21958576e-04, 2.90093082e-03, 9.94503140e-01, 7.88024699e-05,
        2.39518820e-03]], dtype=float32), array([[9.9880111e-01, 4.8

In [ ]:
#accuracy after incrementally training and predicting on x_train_sub[0:500](hold-out set) using loaded_model_shuf1_inc
from sklearn.metrics import accuracy_score
accuracy_score(y_sub_dt[0:2457], m_vote_inc)

0.8656351791530945

In [ ]:
#accuracy after incrementally training and predicting on x_train_sub[0:500](hold-out set) using loaded_model_shuf1_inc
from sklearn.metrics import accuracy_score
accuracy_score(y_sub_dt[0:2457], m_vote)

0.8631921824104235

In [ ]:
from sklearn.metrics import confusion_matrix
matrix = confusion_matrix(y_sub_dt, m_vote_inc)
matrix.diagonal()/matrix.sum(axis=1)

array([0.9572093 , 0.08053691, 0.94899536, 0.86381323, 0.75914634])

In [ ]:
#y_sub_dt
from sklearn.metrics import precision_score, recall_score
f1_cnn = f1_score(y_sub_dt, m_vote_inc, average="macro")
prec_cnn = precision_score(y_sub_dt, m_vote_inc, average="macro")
recall_cnn = recall_score(y_sub_dt, m_vote_inc, average="macro")
if VBS:
    print("Precision: {}".format(prec_cnn)) 
    print("Recall: {}".format(recall_cnn))
    print("F1 score: {}".format(f1_cnn))

    report = classification_report(y_sub_dt, m_vote_inc, digits=6)
    print(report)

Precision: 0.7628605483981545
Recall: 0.7219402298654993
F1 score: 0.7214947838103901
              precision    recall  f1-score   support

           0   0.986577  0.957209  0.971671      1075
           1   0.363636  0.080537  0.131868       149
           2   0.743341  0.948995  0.833673       647
           3   0.932773  0.863813  0.896970       257
           4   0.787975  0.759146  0.773292       328

    accuracy                       0.865635      2456
   macro avg   0.762861  0.721940  0.721495      2456
weighted avg   0.852554  0.865635  0.850058      2456



In [ ]:
x_train_with_semi_sup_labels=x_sub_set

In [ ]:
x_train_with_semi_sup_labels['pseudo_labels']=m_vote_inc

In [ ]:
x_train_with_semi_sup_labels

0         1         2         3         4         5         6  \
0    -0.037317 -0.035184 -0.053523 -0.013007  0.056081  0.106405  0.121332   
1     0.022085 -0.017796 -0.064110 -0.042669 -0.010506  0.002359 -0.012222   
2    -0.127577 -0.109566 -0.066254 -0.008791 -0.037952 -0.106564 -0.128006   
3    -0.147303 -0.149447 -0.105278 -0.070971 -0.057678 -0.042240 -0.037523   
4    -0.071861 -0.088920 -0.128156 -0.128156 -0.117920 -0.088067 -0.066743   
...        ...       ...       ...       ...       ...       ...       ...   
2451 -0.002359  0.139156 -0.008791  0.067970  0.106136  0.143015  0.113426   
2452 -0.136259 -0.109391 -0.123891 -0.130714 -0.159288 -0.149053 -0.161847   
2453  0.016081  0.049101 -0.076117 -0.019083 -0.055534 -0.042669 -0.136583   
2454 -0.009220 -0.006647 -0.006218 -0.010506  0.011364 -0.017368 -0.025515   
2455  0.007890 -0.079964 -0.121332 -0.080390 -0.072714 -0.021963  0.009596   

             7         8         9  ...      2991      2992      2993  \
0     0.129435  0.153744  0.198097  ... -0.088920 -0.118773 -0.130714   
1    -0.040524 -0.072258 -0.054247  ...  0.119858  0.074831 -0.004503   
2    -0.106993 -0.100132 -0.077833  ... -0.001501  0.037952  0.036665   
3    -0.040953 -0.046957 -0.017796  ...  0.239931  0.229639  0.205624   
4    -0.033478 -0.030919 -0.008743  ...  0.031772 -0.009596 -0.039875   
...        ...       ...       ...  ...       ...       ...       ...   
2451  0.005789  0.059822  0.031948  ... -0.274666 -0.113855 -0.155022   
2452 -0.102141 -0.091905 -0.026228  ... -0.175068 -0.268039 -0.137538   
2453 -0.041811 -0.082550 -0.010078  ... -0.121573 -0.110424 -0.085123   
2454 -0.032377 -0.011793  0.010935  ... -0.045242 -0.006218  0.029804   
2455  0.013434  0.027081 -0.027934  ...  0.027508  0.044567  0.044993   

          2994      2995      2996      2997      2998      2999  \
0    -0.128156 -0.092332 -0.072287 -0.056081 -0.107685 -0.138817   
1    -0.031090 -0.081263 -0.052103 -0.084265 -0.057249 -0.053389   
2     0.046528  0.048243  0.011364  0.021656  0.037094  0.021656   
3     0.192759  0.182039  0.137869  0.111710  0.105278  0.122860   
4    -0.053523 -0.083802 -0.053096 -0.012581 -0.015140  0.001919   
...        ...       ...       ...       ...       ...       ...   
2451  0.121145 -0.032377  0.225350 -0.048672 -0.414036 -0.345852   
2452 -0.193406 -0.041581 -0.178906 -0.052243 -0.233495 -0.170376   
2453 -0.070114 -0.073544 -0.042240 -0.027231  0.014366 -0.018225   
2454  0.075260  0.103991  0.104420  0.073544  0.057678  0.033663   
2455  0.051817  0.078685  0.100435  0.136685  0.148626  0.104273   

      pseudo_labels  
0                 2  
1                 2  
2                 4  
3                 2  
4                 2  
...             ...  
2451              0  
2452              0  
2453              1  
2454              2  
2455              2  

[2456 rows x 3001 columns]

In [ ]:
x_train_with_semi_sup_labels.to_csv(r'/content/gdrive/My Drive/physionet/ensemble/50_subs/x_train_with_inc_semi_sup_labels_train_on_batch_trial_4.csv', header=False, index=False)

In [ ]:
#classic incremental learning, not semi supervised inc

In [ ]:
checkpoint_path_model_inc_shuf1 = "/content/gdrive/My Drive/physionet/ensemble_classic_inc/model_shuf1/weights-{epoch:02d}-{accuracy:.3f}.ckpt"
checkpoint_dir_model_inc_shuf1 = os.path.dirname(checkpoint_path_model_inc_shuf1)
cp_callback_model_new_shuf1 = tf.keras.callbacks.ModelCheckpoint(
    filepath=checkpoint_path_model_inc_shuf1,
    monitor='accuracy', 
    verbose=1, 
    save_weights_only=True,
    mode = 'max',
    period=1)

In [ ]:
checkpoint_path_model_inc_shuf2 = "/content/gdrive/My Drive/physionet/ensemble_classic_inc/model_shuf2/weights-{epoch:02d}-{accuracy:.3f}.ckpt"
checkpoint_dir_model_inc_shuf2 = os.path.dirname(checkpoint_path_model_inc_shuf2)
cp_callback_model_new_shuf2 = tf.keras.callbacks.ModelCheckpoint(
    filepath=checkpoint_path_model_inc_shuf2,
    monitor='accuracy', 
    verbose=1, 
    save_weights_only=True,
    mode = 'max',
    period=1)

In [ ]:
checkpoint_path_model_inc_shuf3 = "/content/gdrive/My Drive/physionet/ensemble_classic_inc/model_shuf3/weights-{epoch:02d}-{accuracy:.3f}.ckpt"
checkpoint_dir_model_inc_shuf3 = os.path.dirname(checkpoint_path_model_inc_shuf3)
cp_callback_model_new_shuf3 = tf.keras.callbacks.ModelCheckpoint(
    filepath=checkpoint_path_model_inc_shuf3,
    monitor='accuracy', 
    verbose=1, 
    save_weights_only=True,
    mode = 'max',
    period=1)

In [ ]:
preds_shuf1=[]
preds_inc_shuf1=[]
probabilities_shuf1=[]
probabilities_inc_shuf1=[]


count_shuf1=0

preds_shuf2=[]
preds_inc_shuf2=[]
probabilities_shuf2=[]
probabilities_inc_shuf2=[]

count_shuf2=0

preds_shuf3=[]
preds_inc_shuf3=[]
probabilities_shuf3=[]
probabilities_inc_shuf3=[]

cnt_shuf3=0

m_vote_inc=[]

m_vote=[]

count_status1=0
count_status2=0
count_status3=0

for sple in np.array(x_sub_set[0:2457]):

  sple_rshp=sple.reshape(1,3000,1)



  p1_i=loaded_model_shuf1.predict(sple_rshp)

  p1_i_fin=np.argmax(p1_i,axis=1)

  preds_shuf1.append(np.asscalar(p1_i_fin))

  probabilities_shuf1.append(p1_i) 

  
    
  p1_i_inc=loaded_model_shuf1_new.predict_on_batch(sple_rshp)

  p1_i_inc_fin=np.argmax(p1_i_inc,axis=1)

  

  #count_shuf1+=1

  p2_i=loaded_model_shuf2.predict(sple_rshp)

  p2_i_fin=np.argmax(p2_i,axis=1)

  preds_shuf2.append(np.asscalar(p2_i_fin))

  probabilities_shuf2.append(p2_i)

  
    
  p2_i_inc=loaded_model_shuf2_new.predict_on_batch(sple_rshp)

  p2_i_inc_fin=np.argmax(p2_i_inc,axis=1)

  

  #count_shuf2+=1

  p3_i=loaded_model_shuf3.predict(sple_rshp)

  p3_i_fin=np.argmax(p3_i,axis=1)

  preds_shuf3.append(np.asscalar(p3_i_fin))

  probabilities_shuf3.append(p3_i)

  
    
  p3_i_inc=loaded_model_shuf3_new.predict_on_batch(sple_rshp)

  p3_i_inc_fin=np.argmax(p3_i_inc,axis=1)

  



  preds_inc_shuf1.append(np.asscalar(p1_i_inc_fin))

  probabilities_inc_shuf1.append(p1_i_inc)


  preds_inc_shuf2.append(np.asscalar(p2_i_inc_fin))

  probabilities_inc_shuf2.append(p2_i_inc)


  preds_inc_shuf3.append(np.asscalar(p3_i_inc_fin))

  probabilities_inc_shuf3.append(p3_i_inc)



  mode_i_inc=mode([np.asscalar(p1_i_inc_fin),np.asscalar(p2_i_inc_fin),np.asscalar(p3_i_inc_fin)])
  m_vote_i_inc=mode_i_inc[0][0]
  m_vote_inc.append(m_vote_i_inc)

  mode_i=mode([np.asscalar(p1_i_fin),np.asscalar(p2_i_fin),np.asscalar(p3_i_fin)])
  m_vote_i=mode_i[0][0]
  m_vote.append(m_vote_i)


  p1_i_inc_fin_=np_utils.to_categorical(np.asscalar(p1_i_inc_fin), num_classes=5)
  p2_i_inc_fin_=np_utils.to_categorical(np.asscalar(p2_i_inc_fin), num_classes=5)
  p3_i_inc_fin_=np_utils.to_categorical(np.asscalar(p3_i_inc_fin), num_classes=5)

  p1_i_inc_fin_.shape=(1,5)
  p2_i_inc_fin_.shape=(1,5)
  p3_i_inc_fin_.shape=(1,5)

   

  

  loaded_model_shuf1_new.train_on_batch(sple_rshp, p1_i_inc_fin_)

  

  loaded_model_shuf2_new.train_on_batch(sple_rshp, p2_i_inc_fin_)

  

  loaded_model_shuf3_new.train_on_batch(sple_rshp, p3_i_inc_fin_)




In [ ]:
print(m_vote)
print(m_vote_inc)

[2, 2, 4, 2, 2, 0, 0, 2, 2, 2, 3, 3, 0, 4, 0, 3, 2, 0, 2, 0, 4, 0, 0, 4, 0, 0, 0, 2, 4, 2, 0, 2, 4, 2, 0, 0, 4, 2, 1, 2, 3, 0, 2, 2, 0, 3, 0, 0, 2, 2, 2, 4, 2, 2, 4, 0, 0, 0, 0, 0, 4, 3, 0, 0, 1, 0, 2, 2, 0, 0, 2, 0, 2, 2, 0, 0, 0, 2, 0, 0, 2, 1, 2, 2, 0, 0, 0, 0, 0, 2, 1, 2, 2, 3, 2, 0, 3, 0, 2, 4, 2, 0, 2, 2, 2, 2, 0, 0, 3, 0, 4, 2, 0, 0, 4, 0, 0, 2, 0, 0, 0, 0, 0, 0, 0, 0, 0, 2, 0, 0, 0, 0, 0, 4, 2, 2, 0, 0, 0, 0, 3, 0, 0, 0, 2, 0, 2, 0, 0, 2, 2, 4, 1, 2, 0, 2, 2, 0, 2, 0, 2, 0, 0, 3, 1, 2, 0, 4, 0, 2, 0, 0, 2, 3, 4, 2, 4, 2, 0, 2, 0, 0, 1, 0, 2, 2, 2, 0, 2, 4, 3, 0, 3, 2, 2, 2, 2, 3, 0, 2, 0, 3, 2, 4, 0, 3, 2, 2, 2, 4, 0, 2, 4, 0, 0, 0, 2, 0, 0, 4, 0, 0, 0, 2, 0, 4, 0, 4, 0, 2, 3, 3, 3, 2, 3, 2, 2, 1, 4, 2, 3, 4, 0, 0, 0, 0, 4, 0, 3, 0, 2, 3, 2, 4, 3, 2, 0, 0, 2, 2, 3, 0, 4, 2, 0, 0, 0, 2, 0, 0, 0, 3, 0, 2, 2, 0, 0, 2, 2, 0, 3, 2, 0, 0, 0, 2, 0, 0, 0, 2, 4, 0, 2, 0, 0, 0, 4, 0, 2, 4, 2, 0, 1, 0, 0, 2, 0, 2, 0, 4, 2, 4, 2, 0, 0, 2, 0, 0, 4, 0, 2, 4, 2, 0, 3, 0, 4, 0, 2, 2, 0, 0, 3, 

In [ ]:
print(probabilities_inc_shuf1)
print(probabilities_inc_shuf2)
print(probabilities_inc_shuf3)

Streaming output truncated to the last 5000 lines.
        1.8864380e-03]], dtype=float32), array([[9.9821174e-01, 2.4839528e-04, 5.4496888e-04, 4.0137587e-05,
        9.5477747e-04]], dtype=float32), array([[2.2976375e-05, 1.7898485e-04, 9.9799228e-01, 1.0627198e-04,
        1.6995145e-03]], dtype=float32), array([[9.9853599e-01, 3.1896788e-04, 1.9800203e-04, 5.8057081e-05,
        8.8890170e-04]], dtype=float32), array([[2.8082870e-05, 2.9841581e-04, 9.9829990e-01, 4.3854892e-05,
        1.3296606e-03]], dtype=float32), array([[4.9596918e-05, 2.2772628e-04, 6.7454088e-04, 7.8961903e-06,
        9.9904019e-01]], dtype=float32), array([[9.9915373e-01, 1.7187142e-04, 1.4427301e-04, 9.2647766e-05,
        4.3745432e-04]], dtype=float32), array([[7.4865091e-01, 3.7946473e-03, 1.9245351e-02, 4.9872015e-04,
        2.2781035e-01]], dtype=float32), array([[3.1341242e-05, 2.8765760e-04, 9.9764460e-01, 4.6234003e-05,
        1.9901711e-03]], dtype=float32), array([[9.9772841e-01, 2.5772824e-04

In [ ]:
print(probabilities_shuf1)
print(probabilities_shuf2)
print(probabilities_shuf3)

Streaming output truncated to the last 5000 lines.
        2.8659016e-04]], dtype=float32), array([[9.9893969e-01, 3.2339172e-04, 4.7321085e-04, 9.4169627e-05,
        1.6939642e-04]], dtype=float32), array([[1.6068619e-04, 9.9565112e-04, 8.5320187e-01, 1.4440058e-01,
        1.2412841e-03]], dtype=float32), array([[9.97947156e-01, 1.59555464e-03, 3.31521878e-04, 1.34054735e-05,
        1.12480215e-04]], dtype=float32), array([[2.9182504e-05, 2.3514144e-03, 9.9627328e-01, 5.0847570e-04,
        8.3760306e-04]], dtype=float32), array([[2.3999154e-03, 6.0397599e-02, 2.5356922e-01, 6.2655497e-05,
        6.8357062e-01]], dtype=float32), array([[9.9971205e-01, 1.7999674e-04, 6.9415306e-05, 2.7697135e-05,
        1.0903364e-05]], dtype=float32), array([[9.9420834e-01, 4.1619334e-03, 1.4337291e-03, 4.3201246e-05,
        1.5281708e-04]], dtype=float32), array([[1.2195869e-04, 2.9009322e-03, 9.9450314e-01, 7.8802470e-05,
        2.3951870e-03]], dtype=float32), array([[9.9880111e-01, 4.846755

In [ ]:
#accuracy after incrementally training and predicting on x_train_sub[0:500](hold-out set) using loaded_model_shuf1_inc
from sklearn.metrics import accuracy_score
accuracy_score(y_sub_dt[0:2457], m_vote_inc)

0.7829804560260586

In [ ]:
#accuracy after incrementally training and predicting on x_train_sub[0:500](hold-out set) using loaded_model_shuf1_inc
from sklearn.metrics import accuracy_score
accuracy_score(y_sub_dt[0:2457], m_vote)

0.8631921824104235

In [ ]:
from sklearn.metrics import confusion_matrix
matrix = confusion_matrix(y_sub_dt, m_vote_inc)
matrix.diagonal()/matrix.sum(axis=1)

array([0.93023256, 0.00671141, 0.96290572, 0.12062257, 0.81707317])

In [ ]:
from sklearn.metrics import precision_score, recall_score
f1_cnn = f1_score(y_sub_dt, m_vote_inc, average="macro")
prec_cnn = precision_score(y_sub_dt, m_vote_inc, average="macro")
recall_cnn = recall_score(y_sub_dt, m_vote_inc, average="macro")
if VBS:
    print("Precision: {}".format(prec_cnn)) 
    print("Recall: {}".format(recall_cnn))
    print("F1 score: {}".format(f1_cnn))

    report = classification_report(y_sub_dt, m_vote_inc, digits=6)
    print(report)

Precision: 0.7079358294600021
Recall: 0.5675090850124601
F1 score: 0.5393436174161357
              precision    recall  f1-score   support

           0   0.991080  0.930233  0.959693      1075
           1   0.250000  0.006711  0.013072       149
           2   0.595602  0.962906  0.735972       647
           3   0.968750  0.120623  0.214533       257
           4   0.734247  0.817073  0.773449       328

    accuracy                       0.782980      2456
   macro avg   0.707936  0.567509  0.539344      2456
weighted avg   0.805300  0.782980  0.740479      2456



In [ ]:
x_train_classic_labels=x_sub_set

In [ ]:
x_train_classic_labels['pseudo_labels']=m_vote_inc

In [ ]:
x_train_classic_labels.to_csv(r'/content/gdrive/My Drive/physionet/ensemble/50_subs/x_train_with_classic_labels_trial_10.csv', header=False, index=False)

## simple incremental tri-training 

In [ ]:
checkpoint_path_model_shuf1 = "/content/gdrive/My Drive/physionet/ensemble_simple_inc_tri_train/model_shuf1/weights-{epoch:02d}-{accuracy:.3f}.ckpt"
checkpoint_dir_model_shuf1 = os.path.dirname(checkpoint_path_model_shuf1)
cp_callback_model_shuf1 = tf.keras.callbacks.ModelCheckpoint(
    filepath=checkpoint_path_model_shuf1,
    monitor='accuracy', 
    verbose=1, 
    save_weights_only=True,
    mode = 'max',
    period=1)

In [ ]:
checkpoint_path_model_shuf2 = "/content/gdrive/My Drive/physionet/ensemble_simple_inc_tri_train/model_shuf2/weights-{epoch:02d}-{accuracy:.3f}.ckpt"
checkpoint_dir_model_shuf2 = os.path.dirname(checkpoint_path_model_shuf2)
cp_callback_model_shuf2 = tf.keras.callbacks.ModelCheckpoint(
    filepath=checkpoint_path_model_shuf2,
    monitor='accuracy', 
    verbose=1, 
    save_weights_only=True,
    mode = 'max',
    period=1)

In [ ]:
checkpoint_path_model_shuf3 = "/content/gdrive/My Drive/physionet/ensemble_simple_inc_tri_train/model_shuf3/weights-{epoch:02d}-{accuracy:.3f}.ckpt"
checkpoint_dir_model_shuf3 = os.path.dirname(checkpoint_path_model_shuf3)
cp_callback_model_shuf3 = tf.keras.callbacks.ModelCheckpoint(
    filepath=checkpoint_path_model_shuf3,
    monitor='accuracy', 
    verbose=1, 
    save_weights_only=True,
    mode = 'max',
    period=1)

In [ ]:
preds_shuf1=[]
preds_inc_shuf1=[]
probabilities_shuf1=[]
probabilities_inc_shuf1=[]


count_shuf1=0

preds_shuf2=[]
preds_inc_shuf2=[]
probabilities_shuf2=[]
probabilities_inc_shuf2=[]

count_shuf2=0

preds_shuf3=[]
preds_inc_shuf3=[]
probabilities_shuf3=[]
probabilities_inc_shuf3=[]

cnt_shuf3=0

m_vote_inc=[]

m_vote=[]

count_status1=0
count_status2=0
count_status3=0

for sple in np.array(x_sub_set[0:2457]):

  sple_rshp=sple.reshape(1,3000,1)



  p1_i=loaded_model_shuf1.predict(sple_rshp)

  p1_i_fin=np.argmax(p1_i,axis=1)

  preds_shuf1.append(np.asscalar(p1_i_fin))

  probabilities_shuf1.append(p1_i) 

  
  
  p1_i_inc=loaded_model_shuf1_new.predict_on_batch(sple_rshp)

  p1_i_inc_fin=np.argmax(p1_i_inc,axis=1)

  
  #count_shuf1+=1

  p2_i=loaded_model_shuf2.predict(sple_rshp)

  p2_i_fin=np.argmax(p2_i,axis=1)

  preds_shuf2.append(np.asscalar(p2_i_fin))

  probabilities_shuf2.append(p2_i)

  
    
  p2_i_inc=loaded_model_shuf2_new.predict_on_batch(sple_rshp)

  p2_i_inc_fin=np.argmax(p2_i_inc,axis=1)

  
  #count_shuf2+=1

  p3_i=loaded_model_shuf3.predict(sple_rshp)

  p3_i_fin=np.argmax(p3_i,axis=1)

  preds_shuf3.append(np.asscalar(p3_i_fin))

  probabilities_shuf3.append(p3_i)

  count_status3+=1

  
  p3_i_inc=loaded_model_shuf3_new.predict_on_batch(sple_rshp)

  p3_i_inc_fin=np.argmax(p3_i_inc,axis=1)

  

  preds_inc_shuf1.append(np.asscalar(p1_i_inc_fin))

  probabilities_inc_shuf1.append(p1_i_inc)


  preds_inc_shuf2.append(np.asscalar(p2_i_inc_fin))

  probabilities_inc_shuf2.append(p2_i_inc)


  preds_inc_shuf3.append(np.asscalar(p3_i_inc_fin))

  probabilities_inc_shuf3.append(p3_i_inc)




  mode_i_inc=mode([np.asscalar(p1_i_inc_fin),np.asscalar(p2_i_inc_fin),np.asscalar(p3_i_inc_fin)])
  m_vote_i_inc=mode_i_inc[0][0]
  m_vote_inc.append(m_vote_i_inc)

  mode_i=mode([np.asscalar(p1_i_fin),np.asscalar(p2_i_fin),np.asscalar(p3_i_fin)])
  m_vote_i=mode_i[0][0]
  m_vote.append(m_vote_i)

  #count_shuf3+=1

  #if (p1_i_inc_fin != p1_i_fin):
   # p1_i_inc_fin=p1_i_fin

  #if (p2_i_inc_fin != p2_i_fin):
   # p2_i_inc_fin=p2_i_fin

  #if (p3_i_inc_fin != p3_i_fin):
   # p3_i_inc_fin=p3_i_fin

  
  #p1_i_inc_fin_vals=np.asscalar(p1_i_inc_fin)
  #p2_i_inc_fin_vals=np.asscalar(p2_i_inc_fin)
  #p3_i_inc_fin_vals=np.asscalar(p3_i_inc_fin)

  

  p1_i_inc_fin_=np_utils.to_categorical(np.asscalar(p1_i_inc_fin), num_classes=5)
  p2_i_inc_fin_=np_utils.to_categorical(np.asscalar(p2_i_inc_fin), num_classes=5)
  p3_i_inc_fin_=np_utils.to_categorical(np.asscalar(p3_i_inc_fin), num_classes=5)

  p1_i_inc_fin_.shape=(1,5)
  p2_i_inc_fin_.shape=(1,5)
  p3_i_inc_fin_.shape=(1,5)

  

  if (p2_i_inc_fin==p3_i_inc_fin):
    
    p1_i_inc_fin=p3_i_inc_fin

    p1_i_inc_fin_=np_utils.to_categorical(np.asscalar(p1_i_inc_fin), num_classes=5)

    p1_i_inc_fin_.shape=(1,5)

    #p1_i_inc_fin=np.argmax(p1_i_inc,axis=1)

    
        
    loaded_model_shuf1_new.train_on_batch(sple_rshp, p1_i_inc_fin_)

    

        
   
        
    loaded_model_shuf2_new.train_on_batch(sple_rshp, p2_i_inc_fin_)

   


   
        
    loaded_model_shuf3_new.train_on_batch(sple_rshp, p3_i_inc_fin_)

    
     

  elif (p3_i_inc_fin==p1_i_inc_fin):
    
    p2_i_inc_fin=p1_i_inc_fin

    p2_i_inc_fin_=np_utils.to_categorical(np.asscalar(p2_i_inc_fin), num_classes=5)

    p2_i_inc_fin_.shape=(1,5)

    #p2_i_inc_fin=np.argmax(p2_i_inc,axis=1)

    
        
    loaded_model_shuf2_new.train_on_batch(sple_rshp, p2_i_inc_fin_)

    
   
        
    loaded_model_shuf1_new.train_on_batch(sple_rshp, p1_i_inc_fin_)

    

    
        
    loaded_model_shuf3_new.train_on_batch(sple_rshp, p3_i_inc_fin_)

    
  elif (p2_i_inc_fin==p1_i_inc_fin):
    
    p3_i_inc_fin=p1_i_inc_fin

    p3_i_inc_fin_=np_utils.to_categorical(np.asscalar(p3_i_inc_fin), num_classes=5)

    p3_i_inc_fin_.shape=(1,5)

    #p3_i_inc_fin=np.argmax(p3_i_inc,axis=1)

    
        
    loaded_model_shuf3_new.train_on_batch(sple_rshp, p3_i_inc_fin_)
   


    
        
    loaded_model_shuf1_new.train_on_batch(sple_rshp, p1_i_inc_fin_)

       
    

    
        
    loaded_model_shuf2_new.train_on_batch(sple_rshp, p2_i_inc_fin_)

   
  
 

  else:
 
      
   
        
    loaded_model_shuf1_new.train_on_batch(sple_rshp, p1_i_inc_fin_)

    
    
        
    loaded_model_shuf2_new.train_on_batch(sple_rshp, p2_i_inc_fin_)

    

    
    
        
    loaded_model_shuf3_new.train_on_batch(sple_rshp, p3_i_inc_fin_)

     
  

In [ ]:
print(m_vote)
print(m_vote_inc)

[2, 2, 4, 2, 2, 0, 0, 2, 2, 2, 3, 3, 0, 4, 0, 3, 2, 0, 2, 0, 4, 0, 0, 4, 0, 0, 0, 2, 4, 2, 0, 2, 4, 2, 0, 0, 4, 2, 1, 2, 3, 0, 2, 2, 0, 3, 0, 0, 2, 2, 2, 4, 2, 2, 4, 0, 0, 0, 0, 0, 4, 3, 0, 0, 1, 0, 2, 2, 0, 0, 2, 0, 2, 2, 0, 0, 0, 2, 0, 0, 2, 1, 2, 2, 0, 0, 0, 0, 0, 2, 1, 2, 2, 3, 2, 0, 3, 0, 2, 4, 2, 0, 2, 2, 2, 2, 0, 0, 3, 0, 4, 2, 0, 0, 4, 0, 0, 2, 0, 0, 0, 0, 0, 0, 0, 0, 0, 2, 0, 0, 0, 0, 0, 4, 2, 2, 0, 0, 0, 0, 3, 0, 0, 0, 2, 0, 2, 0, 0, 2, 2, 4, 1, 2, 0, 2, 2, 0, 2, 0, 2, 0, 0, 3, 1, 2, 0, 4, 0, 2, 0, 0, 2, 3, 4, 2, 4, 2, 0, 2, 0, 0, 1, 0, 2, 2, 2, 0, 2, 4, 3, 0, 3, 2, 2, 2, 2, 3, 0, 2, 0, 3, 2, 4, 0, 3, 2, 2, 2, 4, 0, 2, 4, 0, 0, 0, 2, 0, 0, 4, 0, 0, 0, 2, 0, 4, 0, 4, 0, 2, 3, 3, 3, 2, 3, 2, 2, 1, 4, 2, 3, 4, 0, 0, 0, 0, 4, 0, 3, 0, 2, 3, 2, 4, 3, 2, 0, 0, 2, 2, 3, 0, 4, 2, 0, 0, 0, 2, 0, 0, 0, 3, 0, 2, 2, 0, 0, 2, 2, 0, 3, 2, 0, 0, 0, 2, 0, 0, 0, 2, 4, 0, 2, 0, 0, 0, 4, 0, 2, 4, 2, 0, 1, 0, 0, 2, 0, 2, 0, 4, 2, 4, 2, 0, 0, 2, 0, 0, 4, 0, 2, 4, 2, 0, 3, 0, 4, 0, 2, 2, 0, 0, 3, 

In [ ]:
print(probabilities_inc_shuf1)
print(probabilities_inc_shuf2)
print(probabilities_inc_shuf3)

Streaming output truncated to the last 5000 lines.
        9.9611608e-04]], dtype=float32), array([[2.502502e-02, 6.079407e-04, 9.695980e-01, 7.496592e-04,
        4.019412e-03]], dtype=float32), array([[1.3413855e-05, 9.9282137e-05, 9.9914455e-01, 1.2444209e-04,
        6.1833777e-04]], dtype=float32), array([[0.23513432, 0.0020435 , 0.7539933 , 0.00510402, 0.00372497]],
      dtype=float32), array([[1.45789545e-05, 1.46067818e-04, 9.99237776e-01, 4.76890309e-05,
        5.53844671e-04]], dtype=float32), array([[4.1833533e-05, 3.3417152e-04, 2.9402832e-03, 2.7924763e-05,
        9.9665582e-01]], dtype=float32), array([[0.58038855, 0.00344575, 0.408017  , 0.00659574, 0.00155291]],
      dtype=float32), array([[0.00200503, 0.00197619, 0.98231375, 0.00107958, 0.01262546]],
      dtype=float32), array([[1.5903206e-05, 1.4870972e-04, 9.9917859e-01, 3.3541459e-05,
        6.2324223e-04]], dtype=float32), array([[2.7208270e-03, 2.9401455e-04, 9.9422836e-01, 6.1044330e-04,
        2.1464671e-

In [ ]:
print(probabilities_shuf1)
print(probabilities_shuf2)
print(probabilities_shuf3)

Streaming output truncated to the last 5000 lines.
        2.8659016e-04]], dtype=float32), array([[9.9893969e-01, 3.2339172e-04, 4.7321085e-04, 9.4169627e-05,
        1.6939642e-04]], dtype=float32), array([[1.6068632e-04, 9.9565147e-04, 8.5320175e-01, 1.4440064e-01,
        1.2412851e-03]], dtype=float32), array([[9.97947156e-01, 1.59555383e-03, 3.31521878e-04, 1.34054735e-05,
        1.12480113e-04]], dtype=float32), array([[2.9182558e-05, 2.3514153e-03, 9.9627328e-01, 5.0847593e-04,
        8.3760347e-04]], dtype=float32), array([[2.3999154e-03, 6.0397584e-02, 2.5356922e-01, 6.2655497e-05,
        6.8357062e-01]], dtype=float32), array([[9.9971205e-01, 1.7999674e-04, 6.9415306e-05, 2.7697135e-05,
        1.0903364e-05]], dtype=float32), array([[9.9420834e-01, 4.1619376e-03, 1.4337305e-03, 4.3201246e-05,
        1.5281708e-04]], dtype=float32), array([[1.2195881e-04, 2.9009350e-03, 9.9450314e-01, 7.8802543e-05,
        2.3951908e-03]], dtype=float32), array([[9.9880111e-01, 4.846762

In [ ]:
#accuracy after incrementally training and predicting on x_train_sub[0:500](hold-out set) using loaded_model_shuf1_inc
from sklearn.metrics import accuracy_score
accuracy_score(y_sub_dt[0:2457], m_vote_inc)

0.6262214983713354

In [ ]:
#accuracy after incrementally training and predicting on x_train_sub[0:500](hold-out set) using loaded_model_shuf1_inc
from sklearn.metrics import accuracy_score
accuracy_score(y_sub_dt[0:2457], m_vote)

0.8631921824104235

In [ ]:
from sklearn.metrics import confusion_matrix
matrix = confusion_matrix(y_sub_dt, m_vote_inc)
matrix.diagonal()/matrix.sum(axis=1)

array([0.62604651, 0.        , 0.98608964, 0.10116732, 0.61280488])

In [ ]:
from sklearn.metrics import precision_score, recall_score
f1_cnn = f1_score(y_sub_dt, m_vote_inc, average="macro")
prec_cnn = precision_score(y_sub_dt, m_vote_inc, average="macro")
recall_cnn = recall_score(y_sub_dt, m_vote_inc, average="macro")
if VBS:
    print("Precision: {}".format(prec_cnn)) 
    print("Recall: {}".format(recall_cnn))
    print("F1 score: {}".format(f1_cnn))

    report = classification_report(y_sub_dt, m_vote_inc, digits=6)
    print(report)

Precision: 0.6350095821777442
Recall: 0.46522166987298447
F1 score: 0.44730714818861345
              precision    recall  f1-score   support

           0   0.998516  0.626047  0.769583      1075
           1   0.000000  0.000000  0.000000       149
           2   0.425333  0.986090  0.594318       647
           3   0.962963  0.101167  0.183099       257
           4   0.788235  0.612805  0.689537       328

    accuracy                       0.626221      2456
   macro avg   0.635010  0.465222  0.447307      2456
weighted avg   0.755138  0.626221  0.604662      2456



In [ ]:
x_train_with_simple_tri_trained_labels=x_sub_set

In [ ]:
x_train_with_simple_tri_trained_labels['pseudo_labels']=m_vote_inc

In [ ]:
x_train_with_simple_tri_trained_labels.to_csv(r'/content/gdrive/My Drive/physionet/ensemble/50_subs/x_train_with_simple_tri_trained_labels_frozen_layers_train_on_batch_trial_10.csv', header=False, index=False)

##Incremental semi supervised Learning with Tri-Training, majority voting (final modified code)

In [ ]:
checkpoint_path_model_shuf1 = "/content/gdrive/My Drive/physionet/ensemble_inc_semi_sup_tri_train/model_shuf1/weights-{epoch:02d}-{accuracy:.3f}.ckpt"
checkpoint_dir_model_shuf1 = os.path.dirname(checkpoint_path_model_shuf1)
cp_callback_model_shuf1 = tf.keras.callbacks.ModelCheckpoint(
    filepath=checkpoint_path_model_shuf1,
    monitor='accuracy', 
    verbose=1, 
    save_weights_only=True,
    mode = 'max',
    period=1)

In [ ]:
checkpoint_path_model_shuf2 = "/content/gdrive/My Drive/physionet/ensemble_inc_semi_sup_tri_train/model_shuf2/weights-{epoch:02d}-{accuracy:.3f}.ckpt"
checkpoint_dir_model_shuf2 = os.path.dirname(checkpoint_path_model_shuf2)
cp_callback_model_shuf2 = tf.keras.callbacks.ModelCheckpoint(
    filepath=checkpoint_path_model_shuf2,
    monitor='accuracy', 
    verbose=1, 
    save_weights_only=True,
    mode = 'max',
    period=1)

In [ ]:
checkpoint_path_model_shuf3 = "/content/gdrive/My Drive/physionet/ensemble_inc_semi_sup_tri_train/model_shuf3/weights-{epoch:02d}-{accuracy:.3f}.ckpt"
checkpoint_dir_model_shuf3 = os.path.dirname(checkpoint_path_model_shuf3)
cp_callback_model_shuf3 = tf.keras.callbacks.ModelCheckpoint(
    filepath=checkpoint_path_model_shuf3,
    monitor='accuracy', 
    verbose=1, 
    save_weights_only=True,
    mode = 'max',
    period=1)

In [ ]:
preds_shuf1=[]
preds_inc_shuf1=[]
probabilities_shuf1=[]
probabilities_inc_shuf1=[]


count_shuf1=0

preds_shuf2=[]
preds_inc_shuf2=[]
probabilities_shuf2=[]
probabilities_inc_shuf2=[]

count_shuf2=0

preds_shuf3=[]
preds_inc_shuf3=[]
probabilities_shuf3=[]
probabilities_inc_shuf3=[]

cnt_shuf3=0

m_vote_inc=[]

m_vote=[]

count_status1=0
count_status2=0
count_status3=0

for sple in np.array(x_sub_set[0:2457]):

  sple_rshp=sple.reshape(1,3000,1)



  p1_i=loaded_model_shuf1.predict(sple_rshp)

  p1_i_fin=np.argmax(p1_i,axis=1)

  preds_shuf1.append(np.asscalar(p1_i_fin))

  probabilities_shuf1.append(p1_i) 

  
  
  p1_i_inc=loaded_model_shuf1_new.predict_on_batch(sple_rshp)

  p1_i_inc_fin=np.argmax(p1_i_inc,axis=1)

  
  #count_shuf1+=1

  p2_i=loaded_model_shuf2.predict(sple_rshp)

  p2_i_fin=np.argmax(p2_i,axis=1)

  preds_shuf2.append(np.asscalar(p2_i_fin))

  probabilities_shuf2.append(p2_i)

  
    
  p2_i_inc=loaded_model_shuf2_new.predict_on_batch(sple_rshp)

  p2_i_inc_fin=np.argmax(p2_i_inc,axis=1)

  
  #count_shuf2+=1

  p3_i=loaded_model_shuf3.predict(sple_rshp)

  p3_i_fin=np.argmax(p3_i,axis=1)

  preds_shuf3.append(np.asscalar(p3_i_fin))

  probabilities_shuf3.append(p3_i)

  count_status3+=1

  
  p3_i_inc=loaded_model_shuf3_new.predict_on_batch(sple_rshp)

  p3_i_inc_fin=np.argmax(p3_i_inc,axis=1)

  

  preds_inc_shuf1.append(np.asscalar(p1_i_inc_fin))

  probabilities_inc_shuf1.append(p1_i_inc)


  preds_inc_shuf2.append(np.asscalar(p2_i_inc_fin))

  probabilities_inc_shuf2.append(p2_i_inc)


  preds_inc_shuf3.append(np.asscalar(p3_i_inc_fin))

  probabilities_inc_shuf3.append(p3_i_inc)




  mode_i_inc=mode([np.asscalar(p1_i_inc_fin),np.asscalar(p2_i_inc_fin),np.asscalar(p3_i_inc_fin)])
  m_vote_i_inc=mode_i_inc[0][0]
  m_vote_inc.append(m_vote_i_inc)

  mode_i=mode([np.asscalar(p1_i_fin),np.asscalar(p2_i_fin),np.asscalar(p3_i_fin)])
  m_vote_i=mode_i[0][0]
  m_vote.append(m_vote_i)

  #count_shuf3+=1

  if (p1_i_inc_fin != p1_i_fin):
    p1_i_inc_fin=p1_i_fin

  if (p2_i_inc_fin != p2_i_fin):
    p2_i_inc_fin=p2_i_fin

  if (p3_i_inc_fin != p3_i_fin):
    p3_i_inc_fin=p3_i_fin

  
  #p1_i_inc_fin_vals=np.asscalar(p1_i_inc_fin)
  #p2_i_inc_fin_vals=np.asscalar(p2_i_inc_fin)
  #p3_i_inc_fin_vals=np.asscalar(p3_i_inc_fin)

  

  p1_i_inc_fin_=np_utils.to_categorical(np.asscalar(p1_i_inc_fin), num_classes=5)
  p2_i_inc_fin_=np_utils.to_categorical(np.asscalar(p2_i_inc_fin), num_classes=5)
  p3_i_inc_fin_=np_utils.to_categorical(np.asscalar(p3_i_inc_fin), num_classes=5)

  p1_i_inc_fin_.shape=(1,5)
  p2_i_inc_fin_.shape=(1,5)
  p3_i_inc_fin_.shape=(1,5)

  

  if (p2_i_inc_fin==p3_i_inc_fin):
    
    p1_i_inc_fin=p3_i_inc_fin

    p1_i_inc_fin_=np_utils.to_categorical(np.asscalar(p1_i_inc_fin), num_classes=5)

    p1_i_inc_fin_.shape=(1,5)

    #p1_i_inc_fin=np.argmax(p1_i_inc,axis=1)

    
        
    loaded_model_shuf1_new.train_on_batch(sple_rshp, p1_i_inc_fin_)

    

        
   
        
    loaded_model_shuf2_new.train_on_batch(sple_rshp, p2_i_inc_fin_)

   


   
        
    loaded_model_shuf3_new.train_on_batch(sple_rshp, p3_i_inc_fin_)

    
     

  elif (p3_i_inc_fin==p1_i_inc_fin):
    
    p2_i_inc_fin=p1_i_inc_fin

    p2_i_inc_fin_=np_utils.to_categorical(np.asscalar(p2_i_inc_fin), num_classes=5)

    p2_i_inc_fin_.shape=(1,5)

    #p2_i_inc_fin=np.argmax(p2_i_inc,axis=1)

    
        
    loaded_model_shuf2_new.train_on_batch(sple_rshp, p2_i_inc_fin_)

    
   
        
    loaded_model_shuf1_new.train_on_batch(sple_rshp, p1_i_inc_fin_)

    

    
        
    loaded_model_shuf3_new.train_on_batch(sple_rshp, p3_i_inc_fin_)

    
  elif (p2_i_inc_fin==p1_i_inc_fin):
    
    p3_i_inc_fin=p1_i_inc_fin

    p3_i_inc_fin_=np_utils.to_categorical(np.asscalar(p3_i_inc_fin), num_classes=5)

    p3_i_inc_fin_.shape=(1,5)

    #p3_i_inc_fin=np.argmax(p3_i_inc,axis=1)

    
        
    loaded_model_shuf3_new.train_on_batch(sple_rshp, p3_i_inc_fin_)
   


    
        
    loaded_model_shuf1_new.train_on_batch(sple_rshp, p1_i_inc_fin_)

       
    

    
        
    loaded_model_shuf2_new.train_on_batch(sple_rshp, p2_i_inc_fin_)

   
  
 

  else:
 
      
   
        
    loaded_model_shuf1_new.train_on_batch(sple_rshp, p1_i_inc_fin_)

    
    
        
    loaded_model_shuf2_new.train_on_batch(sple_rshp, p2_i_inc_fin_)

    

    
    
        
    loaded_model_shuf3_new.train_on_batch(sple_rshp, p3_i_inc_fin_)

     
  

In [ ]:
print(m_vote)
print(m_vote_inc)

[2, 2, 4, 2, 2, 0, 0, 2, 2, 2, 3, 3, 0, 4, 0, 3, 2, 0, 2, 0, 4, 0, 0, 4, 0, 0, 0, 2, 4, 2, 0, 2, 4, 2, 0, 0, 4, 2, 1, 2, 3, 0, 2, 2, 0, 3, 0, 0, 2, 2, 2, 4, 2, 2, 4, 0, 0, 0, 0, 0, 4, 3, 0, 0, 1, 0, 2, 2, 0, 0, 2, 0, 2, 2, 0, 0, 0, 2, 0, 0, 2, 1, 2, 2, 0, 0, 0, 0, 0, 2, 1, 2, 2, 3, 2, 0, 3, 0, 2, 4, 2, 0, 2, 2, 2, 2, 0, 0, 3, 0, 4, 2, 0, 0, 4, 0, 0, 2, 0, 0, 0, 0, 0, 0, 0, 0, 0, 2, 0, 0, 0, 0, 0, 4, 2, 2, 0, 0, 0, 0, 3, 0, 0, 0, 2, 0, 2, 0, 0, 2, 2, 4, 1, 2, 0, 2, 2, 0, 2, 0, 2, 0, 0, 3, 1, 2, 0, 4, 0, 2, 0, 0, 2, 3, 4, 2, 4, 2, 0, 2, 0, 0, 1, 0, 2, 2, 2, 0, 2, 4, 3, 0, 3, 2, 2, 2, 2, 3, 0, 2, 0, 3, 2, 4, 0, 3, 2, 2, 2, 4, 0, 2, 4, 0, 0, 0, 2, 0, 0, 4, 0, 0, 0, 2, 0, 4, 0, 4, 0, 2, 3, 3, 3, 2, 3, 2, 2, 1, 4, 2, 3, 4, 0, 0, 0, 0, 4, 0, 3, 0, 2, 3, 2, 4, 3, 2, 0, 0, 2, 2, 3, 0, 4, 2, 0, 0, 0, 2, 0, 0, 0, 3, 0, 2, 2, 0, 0, 2, 2, 0, 3, 2, 0, 0, 0, 2, 0, 0, 0, 2, 4, 0, 2, 0, 0, 0, 4, 0, 2, 4, 2, 0, 1, 0, 0, 2, 0, 2, 0, 4, 2, 4, 2, 0, 0, 2, 0, 0, 4, 0, 2, 4, 2, 0, 3, 0, 4, 0, 2, 2, 0, 0, 3, 

In [ ]:
print(probabilities_inc_shuf1)
print(probabilities_inc_shuf2)
print(probabilities_inc_shuf3)

Streaming output truncated to the last 5000 lines.
        3.4550070e-05]], dtype=float32), array([[9.9972492e-01, 1.7359968e-04, 4.1557847e-05, 2.4790372e-05,
        3.5080324e-05]], dtype=float32), array([[2.2191969e-05, 9.1538392e-04, 9.9572158e-01, 2.3044702e-03,
        1.0363255e-03]], dtype=float32), array([[9.9953043e-01, 3.3996245e-04, 6.1429360e-05, 4.0436276e-05,
        2.7802182e-05]], dtype=float32), array([[1.0759518e-05, 5.1535643e-04, 9.9829465e-01, 8.0095022e-04,
        3.7834063e-04]], dtype=float32), array([[2.0406397e-04, 7.1087773e-03, 5.2413237e-01, 1.6766861e-04,
        4.6838713e-01]], dtype=float32), array([[9.9972123e-01, 1.8538408e-04, 3.6143298e-05, 4.3316359e-05,
        1.3819544e-05]], dtype=float32), array([[9.9600488e-01, 2.9576803e-03, 7.2204106e-04, 1.3711021e-04,
        1.7828889e-04]], dtype=float32), array([[1.8584060e-05, 7.5090904e-04, 9.9787867e-01, 1.2804316e-04,
        1.2238752e-03]], dtype=float32), array([[9.9966943e-01, 2.3894208e-04

In [ ]:
print(probabilities_shuf1)
print(probabilities_shuf2)
print(probabilities_shuf3)

Streaming output truncated to the last 5000 lines.
        2.8658993e-04]], dtype=float32), array([[9.9893969e-01, 3.2339172e-04, 4.7321085e-04, 9.4169627e-05,
        1.6939642e-04]], dtype=float32), array([[1.6068602e-04, 9.9565065e-04, 8.5320187e-01, 1.4440058e-01,
        1.2412835e-03]], dtype=float32), array([[9.97947156e-01, 1.59555301e-03, 3.31521558e-04, 1.34054735e-05,
        1.12480004e-04]], dtype=float32), array([[2.9182529e-05, 2.3514153e-03, 9.9627328e-01, 5.0847570e-04,
        8.3760347e-04]], dtype=float32), array([[2.3999158e-03, 6.0397580e-02, 2.5356913e-01, 6.2655454e-05,
        6.8357074e-01]], dtype=float32), array([[9.9971205e-01, 1.7999674e-04, 6.9415240e-05, 2.7697135e-05,
        1.0903364e-05]], dtype=float32), array([[9.9420834e-01, 4.1619278e-03, 1.4337271e-03, 4.3201246e-05,
        1.5281695e-04]], dtype=float32), array([[1.21958576e-04, 2.90093082e-03, 9.94503140e-01, 7.88024699e-05,
        2.39518820e-03]], dtype=float32), array([[9.9880111e-01, 4.8

In [ ]:
#accuracy after incrementally training and predicting on x_train_sub[0:500](hold-out set) using loaded_model_shuf1_inc
from sklearn.metrics import accuracy_score
accuracy_score(y_sub_dt[0:2457], m_vote_inc)

0.8578990228013029

In [ ]:
#accuracy after incrementally training and predicting on x_train_sub[0:500](hold-out set) using loaded_model_shuf1_inc
from sklearn.metrics import accuracy_score
accuracy_score(y_sub_dt[0:2457], m_vote)

0.8631921824104235

In [ ]:
from sklearn.metrics import confusion_matrix
matrix = confusion_matrix(y_sub_dt, m_vote_inc)
matrix.diagonal()/matrix.sum(axis=1)

array([0.94976744, 0.06040268, 0.95054096, 0.84046693, 0.75      ])

In [ ]:
#y_sub_dt
from sklearn.metrics import precision_score, recall_score
f1_cnn = f1_score(y_sub_dt, m_vote_inc, average="macro")
prec_cnn = precision_score(y_sub_dt, m_vote_inc, average="macro")
recall_cnn = recall_score(y_sub_dt, m_vote_inc, average="macro")
if VBS:
    print("Precision: {}".format(prec_cnn)) 
    print("Recall: {}".format(recall_cnn))
    print("F1 score: {}".format(f1_cnn))

    report = classification_report(y_sub_dt, m_vote_inc, digits=6)
    print(report)

Precision: 0.7371363755972192
Recall: 0.7102356021526393
F1 score: 0.7086022296647663
              precision    recall  f1-score   support

           0   0.988383  0.949767  0.968691      1075
           1   0.250000  0.060403  0.097297       149
           2   0.732143  0.950541  0.827169       647
           3   0.939130  0.840467  0.887064       257
           4   0.776025  0.750000  0.762791       328

    accuracy                       0.857899      2456
   macro avg   0.737136  0.710236  0.708602      2456
weighted avg   0.842570  0.857899  0.842504      2456



In [ ]:
x_sub_set

0         1         2         3         4         5         6     \
0    -0.037317 -0.035184 -0.053523 -0.013007  0.056081  0.106405  0.121332   
1     0.022085 -0.017796 -0.064110 -0.042669 -0.010506  0.002359 -0.012222   
2    -0.127577 -0.109566 -0.066254 -0.008791 -0.037952 -0.106564 -0.128006   
3    -0.147303 -0.149447 -0.105278 -0.070971 -0.057678 -0.042240 -0.037523   
4    -0.071861 -0.088920 -0.128156 -0.128156 -0.117920 -0.088067 -0.066743   
...        ...       ...       ...       ...       ...       ...       ...   
2451 -0.002359  0.139156 -0.008791  0.067970  0.106136  0.143015  0.113426   
2452 -0.136259 -0.109391 -0.123891 -0.130714 -0.159288 -0.149053 -0.161847   
2453  0.016081  0.049101 -0.076117 -0.019083 -0.055534 -0.042669 -0.136583   
2454 -0.009220 -0.006647 -0.006218 -0.010506  0.011364 -0.017368 -0.025515   
2455  0.007890 -0.079964 -0.121332 -0.080390 -0.072714 -0.021963  0.009596   

          7         8         9     ...      2990      2991      2992  \
0     0.129435  0.153744  0.198097  ... -0.060773 -0.088920 -0.118773   
1    -0.040524 -0.072258 -0.054247  ...  0.101847  0.119858  0.074831   
2    -0.106993 -0.100132 -0.077833  ... -0.014366 -0.001501  0.037952   
3    -0.040953 -0.046957 -0.017796  ...  0.238644  0.239931  0.229639   
4    -0.033478 -0.030919 -0.008743  ...  0.022390  0.031772 -0.009596   
...        ...       ...       ...  ...       ...       ...       ...   
2451  0.005789  0.059822  0.031948  ... -0.052532 -0.274666 -0.113855   
2452 -0.102141 -0.091905 -0.026228  ... -0.323481 -0.175068 -0.268039   
2453 -0.041811 -0.082550 -0.010078  ... -0.097559 -0.121573 -0.110424   
2454 -0.032377 -0.011793  0.010935  ... -0.072258 -0.045242 -0.006218   
2455  0.013434  0.027081 -0.027934  ... -0.025375  0.027508  0.044567   

          2993      2994      2995      2996      2997      2998      2999  
0    -0.130714 -0.128156 -0.092332 -0.072287 -0.056081 -0.107685 -0.138817  
1    -0.004503 -0.031090 -0.081263 -0.052103 -0.084265 -0.057249 -0.053389  
2     0.036665  0.046528  0.048243  0.011364  0.021656  0.037094  0.021656  
3     0.205624  0.192759  0.182039  0.137869  0.111710  0.105278  0.122860  
4    -0.039875 -0.053523 -0.083802 -0.053096 -0.012581 -0.015140  0.001919  
...        ...       ...       ...       ...       ...       ...       ...  
2451 -0.155022  0.121145 -0.032377  0.225350 -0.048672 -0.414036 -0.345852  
2452 -0.137538 -0.193406 -0.041581 -0.178906 -0.052243 -0.233495 -0.170376  
2453 -0.085123 -0.070114 -0.073544 -0.042240 -0.027231  0.014366 -0.018225  
2454  0.029804  0.075260  0.103991  0.104420  0.073544  0.057678  0.033663  
2455  0.044993  0.051817  0.078685  0.100435  0.136685  0.148626  0.104273  

[2456 rows x 3000 columns]

In [ ]:
x_train_with_tri_trained_labels=x_sub_set

In [ ]:
x_train_with_tri_trained_labels['pseudo_labels']=m_vote_inc

In [ ]:
x_train_with_tri_trained_labels

0         1         2         3         4         5         6  \
0    -0.037317 -0.035184 -0.053523 -0.013007  0.056081  0.106405  0.121332   
1     0.022085 -0.017796 -0.064110 -0.042669 -0.010506  0.002359 -0.012222   
2    -0.127577 -0.109566 -0.066254 -0.008791 -0.037952 -0.106564 -0.128006   
3    -0.147303 -0.149447 -0.105278 -0.070971 -0.057678 -0.042240 -0.037523   
4    -0.071861 -0.088920 -0.128156 -0.128156 -0.117920 -0.088067 -0.066743   
...        ...       ...       ...       ...       ...       ...       ...   
2451 -0.002359  0.139156 -0.008791  0.067970  0.106136  0.143015  0.113426   
2452 -0.136259 -0.109391 -0.123891 -0.130714 -0.159288 -0.149053 -0.161847   
2453  0.016081  0.049101 -0.076117 -0.019083 -0.055534 -0.042669 -0.136583   
2454 -0.009220 -0.006647 -0.006218 -0.010506  0.011364 -0.017368 -0.025515   
2455  0.007890 -0.079964 -0.121332 -0.080390 -0.072714 -0.021963  0.009596   

             7         8         9  ...      2991      2992      2993  \
0     0.129435  0.153744  0.198097  ... -0.088920 -0.118773 -0.130714   
1    -0.040524 -0.072258 -0.054247  ...  0.119858  0.074831 -0.004503   
2    -0.106993 -0.100132 -0.077833  ... -0.001501  0.037952  0.036665   
3    -0.040953 -0.046957 -0.017796  ...  0.239931  0.229639  0.205624   
4    -0.033478 -0.030919 -0.008743  ...  0.031772 -0.009596 -0.039875   
...        ...       ...       ...  ...       ...       ...       ...   
2451  0.005789  0.059822  0.031948  ... -0.274666 -0.113855 -0.155022   
2452 -0.102141 -0.091905 -0.026228  ... -0.175068 -0.268039 -0.137538   
2453 -0.041811 -0.082550 -0.010078  ... -0.121573 -0.110424 -0.085123   
2454 -0.032377 -0.011793  0.010935  ... -0.045242 -0.006218  0.029804   
2455  0.013434  0.027081 -0.027934  ...  0.027508  0.044567  0.044993   

          2994      2995      2996      2997      2998      2999  \
0    -0.128156 -0.092332 -0.072287 -0.056081 -0.107685 -0.138817   
1    -0.031090 -0.081263 -0.052103 -0.084265 -0.057249 -0.053389   
2     0.046528  0.048243  0.011364  0.021656  0.037094  0.021656   
3     0.192759  0.182039  0.137869  0.111710  0.105278  0.122860   
4    -0.053523 -0.083802 -0.053096 -0.012581 -0.015140  0.001919   
...        ...       ...       ...       ...       ...       ...   
2451  0.121145 -0.032377  0.225350 -0.048672 -0.414036 -0.345852   
2452 -0.193406 -0.041581 -0.178906 -0.052243 -0.233495 -0.170376   
2453 -0.070114 -0.073544 -0.042240 -0.027231  0.014366 -0.018225   
2454  0.075260  0.103991  0.104420  0.073544  0.057678  0.033663   
2455  0.051817  0.078685  0.100435  0.136685  0.148626  0.104273   

      pseudo_labels  
0                 2  
1                 2  
2                 4  
3                 2  
4                 2  
...             ...  
2451              0  
2452              0  
2453              1  
2454              2  
2455              2  

[2456 rows x 3001 columns]

In [ ]:
x_train_with_tri_trained_labels.to_csv(r'/content/gdrive/My Drive/physionet/ensemble/50_subs/x_train_with_semi_sup_tri-trained_labels_frozen_layers_train_on_batch_trial_3.csv', header=False, index=False)

appending the subject specific (train data,tri-trained labels) to the (transfer set, maj_labels) 

In [ ]:
transfer_set=pd.read_csv('/content/gdrive/My Drive/physionet/ensemble/50_subs/transfer_set_50_subs.csv',header=None)

In [ ]:
sub_set_with_semi_sup_tri_trained_labels=pd.read_csv('/content/gdrive/My Drive/physionet/ensemble/50_subs/x_train_with_semi_sup_tri-trained_labels_frozen_layers_train_on_batch_trial_1.csv',header=None)

In [ ]:
transfer_set_new=transfer_set.append(sub_set_with_semi_sup_tri_trained_labels, ignore_index=True)

In [ ]:
transfer_set_new.to_csv(r'/content/gdrive/My Drive/physionet/ensemble/50_subs/transfer_set_plus_sub_dt_with_tri_trained_labels_keras_way.csv', header=False, index=False)

In [ ]:
transfer_dt_plus_sub_dt=pd.read_csv('/content/gdrive/My Drive/physionet/ensemble/50_subs/transfer_set_plus_sub_dt_with_tri_trained_labels_keras_way.csv',header=None)

In [ ]:
transfer_dt_plus_sub_dt

0         1         2         3         4         5         6     \
0       0.068014  0.082915  0.077628  0.074744  0.060804  0.063688  0.050710   
1       0.104729  0.054513 -0.020131 -0.064918 -0.122825 -0.127801 -0.107443   
2       0.002281 -0.031309 -0.007672 -0.020527 -0.003110 -0.011404  0.006013   
3      -0.025235 -0.037732 -0.033406 -0.031964 -0.034848 -0.041097 -0.031484   
4       0.097914 -0.100520 -0.044574 -0.079540 -0.071235 -0.029713 -0.041951   
...          ...       ...       ...       ...       ...       ...       ...   
119169 -0.002359  0.139156 -0.008791  0.067970  0.106136  0.143015  0.113426   
119170 -0.136259 -0.109391 -0.123891 -0.130714 -0.159288 -0.149053 -0.161847   
119171  0.016081  0.049101 -0.076117 -0.019083 -0.055534 -0.042669 -0.136583   
119172 -0.009220 -0.006647 -0.006218 -0.010506  0.011364 -0.017368 -0.025515   
119173  0.007890 -0.079964 -0.121332 -0.080390 -0.072714 -0.021963  0.009596   

            7         8         9     ...      2991      2992      2993  \
0       0.029561  0.010815  0.008412  ... -0.010334 -0.016102 -0.034368   
1      -0.086633 -0.051799 -0.033251  ... -0.123729 -0.120563 -0.129158   
2      -0.029236 -0.025089 -0.042091  ...  0.088122  0.057850  0.027992   
3      -0.025716 -0.019948 -0.030522  ... -0.015141 -0.013699 -0.018025   
4       0.000445 -0.031024  0.172217  ...  0.167409  0.220732  0.191011   
...          ...       ...       ...  ...       ...       ...       ...   
119169  0.005789  0.059822  0.031948  ... -0.274666 -0.113855 -0.155022   
119170 -0.102141 -0.091905 -0.026228  ... -0.175068 -0.268039 -0.137538   
119171 -0.041811 -0.082550 -0.010078  ... -0.121573 -0.110424 -0.085123   
119172 -0.032377 -0.011793  0.010935  ... -0.045242 -0.006218  0.029804   
119173  0.013434  0.027081 -0.027934  ...  0.027508  0.044567  0.044993   

            2994      2995      2996      2997      2998      2999  3000  
0      -0.055998 -0.074263 -0.071860 -0.077147 -0.084838 -0.090125     4  
1      -0.149968 -0.173945 -0.187064 -0.171231 -0.149516 -0.121467     3  
2       0.038359  0.040847  0.053703  0.072779  0.055362  0.029651     2  
3      -0.020909 -0.021390 -0.002644 -0.020428 -0.025235 -0.024754     2  
4       0.119767  0.165661  0.270996  0.200190  0.246520  0.166535     0  
...          ...       ...       ...       ...       ...       ...   ...  
119169  0.121145 -0.032377  0.225350 -0.048672 -0.414036 -0.345852     0  
119170 -0.193406 -0.041581 -0.178906 -0.052243 -0.233495 -0.170376     0  
119171 -0.070114 -0.073544 -0.042240 -0.027231  0.014366 -0.018225     0  
119172  0.075260  0.103991  0.104420  0.073544  0.057678  0.033663     2  
119173  0.051817  0.078685  0.100435  0.136685  0.148626  0.104273     2  

[119174 rows x 3001 columns]

In [ ]:
transfer_set

0         1         2         3         4         5         6     \
0       0.068014  0.082915  0.077628  0.074744  0.060804  0.063688  0.050710   
1       0.104729  0.054513 -0.020131 -0.064918 -0.122825 -0.127801 -0.107443   
2       0.002281 -0.031309 -0.007672 -0.020527 -0.003110 -0.011404  0.006013   
3      -0.025235 -0.037732 -0.033406 -0.031964 -0.034848 -0.041097 -0.031484   
4       0.097914 -0.100520 -0.044574 -0.079540 -0.071235 -0.029713 -0.041951   
...          ...       ...       ...       ...       ...       ...       ...   
116713  0.032558  0.033944  0.046413  0.056111  0.060267  0.066271  0.077816   
116714  0.068695  0.059483  0.051071  0.044662  0.037051  0.041057  0.040656   
116715  0.013392  0.030717  0.029805  0.016127  0.026613  0.024334  0.019775   
116716 -0.057457 -0.065629 -0.101198 -0.114176 -0.141093 -0.184354 -0.222807   
116717 -0.065742 -0.082698 -0.086365 -0.053368 -0.023122 -0.024038 -0.046494   

            7         8         9     ...      2991      2992      2993  \
0       0.029561  0.010815  0.008412  ... -0.010334 -0.016102 -0.034368   
1      -0.086633 -0.051799 -0.033251  ... -0.123729 -0.120563 -0.129158   
2      -0.029236 -0.025089 -0.042091  ...  0.088122  0.057850  0.027992   
3      -0.025716 -0.019948 -0.030522  ... -0.015141 -0.013699 -0.018025   
4       0.000445 -0.031024  0.172217  ...  0.167409  0.220732  0.191011   
...          ...       ...       ...  ...       ...       ...       ...   
116713  0.058882  0.078278  0.051493  ...  0.024707  0.025631  0.015933   
116714  0.046264  0.039054  0.045063  ...  0.035850  0.031444  0.026637   
116715  0.038012  0.027069  0.031629  ...  0.013392  0.018863  0.034820   
116716 -0.230017 -0.242514 -0.231459  ... -0.085817 -0.068993 -0.058899   
116717 -0.133109 -0.211476 -0.300383  ... -0.135401 -0.128985 -0.091864   

            2994      2995      2996      2997      2998      2999  3000  
0      -0.055998 -0.074263 -0.071860 -0.077147 -0.084838 -0.090125     4  
1      -0.149968 -0.173945 -0.187064 -0.171231 -0.149516 -0.121467     3  
2       0.038359  0.040847  0.053703  0.072779  0.055362  0.029651     2  
3      -0.020909 -0.021390 -0.002644 -0.020428 -0.025235 -0.024754     2  
4       0.119767  0.165661  0.270996  0.200190  0.246520  0.166535     0  
...          ...       ...       ...       ...       ...       ...   ...  
116713  0.044565 -0.000231  0.018242 -0.028402  0.021475  0.028402     2  
116714  0.023433  0.027839  0.023833  0.018626  0.005007  0.007010     4  
116715  0.034364  0.042115  0.045306  0.041659  0.032996  0.024334     4  
116716 -0.043999 -0.058419 -0.065629 -0.070916 -0.068513 -0.090143     2  
116717 -0.071700 -0.102404 -0.157398 -0.150524 -0.087281 -0.042828     2  

[116718 rows x 3001 columns]

trial 2,3

In [ ]:
sub_set_with_semi_sup_tri_trained_labels=pd.read_csv('/content/gdrive/My Drive/physionet/ensemble/50_subs/x_train_with_semi_sup_tri-trained_labels_frozen_layers_train_on_batch_trial_3.csv',header=None)

In [ ]:
transfer_set_new=transfer_set.append(sub_set_with_semi_sup_tri_trained_labels, ignore_index=True)

In [ ]:
transfer_set_new.to_csv(r'/content/gdrive/My Drive/physionet/ensemble/50_subs/transfer_set_plus_sub_dt_with_tri_trained_labels_keras_way_sub_482_trial_3.csv', header=False, index=False)

In [ ]:
transfer_dt_plus_sub_dt=pd.read_csv('/content/gdrive/My Drive/physionet/ensemble/50_subs/transfer_set_plus_sub_dt_with_tri_trained_labels_keras_way_sub_482_trial_3.csv',header=None)

In [ ]:
transfer_dt_plus_sub_dt

0         1         2         3         4         5         6     \
0       0.068014  0.082915  0.077628  0.074744  0.060804  0.063688  0.050710   
1       0.104729  0.054513 -0.020131 -0.064918 -0.122825 -0.127801 -0.107443   
2       0.002281 -0.031309 -0.007672 -0.020527 -0.003110 -0.011404  0.006013   
3      -0.025235 -0.037732 -0.033406 -0.031964 -0.034848 -0.041097 -0.031484   
4       0.097914 -0.100520 -0.044574 -0.079540 -0.071235 -0.029713 -0.041951   
...          ...       ...       ...       ...       ...       ...       ...   
119169 -0.002359  0.139156 -0.008791  0.067970  0.106136  0.143015  0.113426   
119170 -0.136259 -0.109391 -0.123891 -0.130714 -0.159288 -0.149053 -0.161847   
119171  0.016081  0.049101 -0.076117 -0.019083 -0.055534 -0.042669 -0.136583   
119172 -0.009220 -0.006647 -0.006218 -0.010506  0.011364 -0.017368 -0.025515   
119173  0.007890 -0.079964 -0.121332 -0.080390 -0.072714 -0.021963  0.009596   

            7         8         9     ...      2991      2992      2993  \
0       0.029561  0.010815  0.008412  ... -0.010334 -0.016102 -0.034368   
1      -0.086633 -0.051799 -0.033251  ... -0.123729 -0.120563 -0.129158   
2      -0.029236 -0.025089 -0.042091  ...  0.088122  0.057850  0.027992   
3      -0.025716 -0.019948 -0.030522  ... -0.015141 -0.013699 -0.018025   
4       0.000445 -0.031024  0.172217  ...  0.167409  0.220732  0.191011   
...          ...       ...       ...  ...       ...       ...       ...   
119169  0.005789  0.059822  0.031948  ... -0.274666 -0.113855 -0.155022   
119170 -0.102141 -0.091905 -0.026228  ... -0.175068 -0.268039 -0.137538   
119171 -0.041811 -0.082550 -0.010078  ... -0.121573 -0.110424 -0.085123   
119172 -0.032377 -0.011793  0.010935  ... -0.045242 -0.006218  0.029804   
119173  0.013434  0.027081 -0.027934  ...  0.027508  0.044567  0.044993   

            2994      2995      2996      2997      2998      2999  3000  
0      -0.055998 -0.074263 -0.071860 -0.077147 -0.084838 -0.090125     4  
1      -0.149968 -0.173945 -0.187064 -0.171231 -0.149516 -0.121467     3  
2       0.038359  0.040847  0.053703  0.072779  0.055362  0.029651     2  
3      -0.020909 -0.021390 -0.002644 -0.020428 -0.025235 -0.024754     2  
4       0.119767  0.165661  0.270996  0.200190  0.246520  0.166535     0  
...          ...       ...       ...       ...       ...       ...   ...  
119169  0.121145 -0.032377  0.225350 -0.048672 -0.414036 -0.345852     0  
119170 -0.193406 -0.041581 -0.178906 -0.052243 -0.233495 -0.170376     0  
119171 -0.070114 -0.073544 -0.042240 -0.027231  0.014366 -0.018225     1  
119172  0.075260  0.103991  0.104420  0.073544  0.057678  0.033663     2  
119173  0.051817  0.078685  0.100435  0.136685  0.148626  0.104273     2  

[119174 rows x 3001 columns]

In [ ]:
transfer_set_new

0         1         2         3         4         5         6     \
0       0.068014  0.082915  0.077628  0.074744  0.060804  0.063688  0.050710   
1       0.104729  0.054513 -0.020131 -0.064918 -0.122825 -0.127801 -0.107443   
2       0.002281 -0.031309 -0.007672 -0.020527 -0.003110 -0.011404  0.006013   
3      -0.025235 -0.037732 -0.033406 -0.031964 -0.034848 -0.041097 -0.031484   
4       0.097914 -0.100520 -0.044574 -0.079540 -0.071235 -0.029713 -0.041951   
...          ...       ...       ...       ...       ...       ...       ...   
119169 -0.002359  0.139156 -0.008791  0.067970  0.106136  0.143015  0.113426   
119170 -0.136259 -0.109391 -0.123891 -0.130714 -0.159288 -0.149053 -0.161847   
119171  0.016081  0.049101 -0.076117 -0.019083 -0.055534 -0.042669 -0.136583   
119172 -0.009220 -0.006647 -0.006218 -0.010506  0.011364 -0.017368 -0.025515   
119173  0.007890 -0.079964 -0.121332 -0.080390 -0.072714 -0.021963  0.009596   

            7         8         9     ...      2991      2992      2993  \
0       0.029561  0.010815  0.008412  ... -0.010334 -0.016102 -0.034368   
1      -0.086633 -0.051799 -0.033251  ... -0.123729 -0.120563 -0.129158   
2      -0.029236 -0.025089 -0.042091  ...  0.088122  0.057850  0.027992   
3      -0.025716 -0.019948 -0.030522  ... -0.015141 -0.013699 -0.018025   
4       0.000445 -0.031024  0.172217  ...  0.167409  0.220732  0.191011   
...          ...       ...       ...  ...       ...       ...       ...   
119169  0.005789  0.059822  0.031948  ... -0.274666 -0.113855 -0.155022   
119170 -0.102141 -0.091905 -0.026228  ... -0.175068 -0.268039 -0.137538   
119171 -0.041811 -0.082550 -0.010078  ... -0.121573 -0.110424 -0.085123   
119172 -0.032377 -0.011793  0.010935  ... -0.045242 -0.006218  0.029804   
119173  0.013434  0.027081 -0.027934  ...  0.027508  0.044567  0.044993   

            2994      2995      2996      2997      2998      2999  3000  
0      -0.055998 -0.074263 -0.071860 -0.077147 -0.084838 -0.090125     4  
1      -0.149968 -0.173945 -0.187064 -0.171231 -0.149516 -0.121467     3  
2       0.038359  0.040847  0.053703  0.072779  0.055362  0.029651     2  
3      -0.020909 -0.021390 -0.002644 -0.020428 -0.025235 -0.024754     2  
4       0.119767  0.165661  0.270996  0.200190  0.246520  0.166535     0  
...          ...       ...       ...       ...       ...       ...   ...  
119169  0.121145 -0.032377  0.225350 -0.048672 -0.414036 -0.345852     0  
119170 -0.193406 -0.041581 -0.178906 -0.052243 -0.233495 -0.170376     0  
119171 -0.070114 -0.073544 -0.042240 -0.027231  0.014366 -0.018225     1  
119172  0.075260  0.103991  0.104420  0.073544  0.057678  0.033663     2  
119173  0.051817  0.078685  0.100435  0.136685  0.148626  0.104273     2  

[119174 rows x 3001 columns]